# RDS Data Loader

In [1]:
from typing import List, Tuple
import requests
import json
import numpy as np
from concurrent.futures import ThreadPoolExecutor, as_completed
from datetime import datetime
import pandas as pd

In [2]:
BASE_URL = "https://xug11cb2b1.execute-api.eu-central-1.amazonaws.com/dev/"
CSV_PATH = "./csv_test/"

In [3]:
def send_request(endpoint: str, base_url: str = BASE_URL):
    url = f"{base_url}{endpoint}"
    response = requests.get(url)
    
    if response.status_code != 200:
        response.raise_for_status()

    return response.json()

In [4]:
def post_request(endpoint: str, data: dict | list, base_url: str = BASE_URL):
    url = f"{base_url}{endpoint}"
    headers = {'Content-Type': 'application/json'}
    response = requests.post(url, headers=headers, data=json.dumps(data))
    
    if response.status_code == 201 or response.status_code == 207:
        return response.json()
    else:
        print(response.json())
        response.raise_for_status()

In [5]:
def delete_request(endpoint: str, id: int, base_url: str = BASE_URL):
    if not endpoint.endswith('/'):
        endpoint += '/'
    url = f"{base_url}{endpoint}{id}"
    data = {"confirmDelete": True}
    
    response = requests.delete(url, json=data)
    
    if response.status_code == 200:
        return response.json()
    else:
        response.raise_for_status()

In [6]:
def chunked(iterable: List, size: int):
    """Yield successive chunks from iterable of given size."""
    for i in range(0, len(iterable), size):
        data = iterable[i:i + size]
        yield data

CHUNK_SIZE = 5

## Healt Check

In [7]:
endpoint = "/db/health"

data = send_request(endpoint)
data

{'success': True,
 'message': 'Health check completed',
 'data': {'service': 'M4ESTRO Database API',
  'version': '1.0.0',
  'requestId': 'req_1753773191041_c4szhhbij',
  'health': {'status': 'healthy',
   'timestamp': '2025-07-29T07:13:11.301Z',
   'database': 'maestroApp',
   'tableCount': 41,
   'connectionPool': {'min': 0, 'max': 1, 'used': 0, 'waiting': 0}},
  'statistics': {'summary': {'totalTables': 36,
    'existingTables': 0,
    'totalRows': 0,
    'totalSizeKB': 0,
    'totalSizeMB': 0},
   'tables': [{'tableName': 'route_orders',
     'exists': False,
     'error': '(intermediate value) is not iterable'},
    {'tableName': 'routes',
     'exists': False,
     'error': '(intermediate value) is not iterable'},
    {'tableName': 'vertices',
     'exists': False,
     'error': '(intermediate value) is not iterable'},
    {'tableName': 'orders',
     'exists': False,
     'error': '(intermediate value) is not iterable'},
    {'tableName': 'order_steps_enriched',
     'exists': F

## Tables

In [8]:
endpoint = "/db/tables"

data = send_request(endpoint)
data

{'success': True,
 'message': 'Retrieved info for 36 tables',
 'data': {'totalTables': 36,
  'tables': [{'tableName': 'alphas', 'rowCount': 0},
   {'tableName': 'alphas_opt', 'rowCount': 0},
   {'tableName': 'carriers', 'rowCount': 0},
   {'tableName': 'countries', 'rowCount': 0},
   {'tableName': 'dispatch_time_gammas', 'rowCount': 0},
   {'tableName': 'dispatch_time_samples', 'rowCount': 0},
   {'tableName': 'dispatch_times', 'rowCount': 0},
   {'tableName': 'disruptions', 'rowCount': 0},
   {'tableName': 'estimated_times', 'rowCount': 0},
   {'tableName': 'estimated_times_holidays', 'rowCount': 0},
   {'tableName': 'estimation_params', 'rowCount': 0},
   {'tableName': 'holidays', 'rowCount': 0},
   {'tableName': 'kafka_disruption', 'rowCount': 0},
   {'tableName': 'locations', 'rowCount': 0},
   {'tableName': 'manufacturers', 'rowCount': 0},
   {'tableName': 'order_step_weather_data', 'rowCount': 0},
   {'tableName': 'order_steps', 'rowCount': 0},
   {'tableName': 'order_steps_enric

## Data insertion

### Country

In [9]:
endpoint = "db/tables/countries"

In [10]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('countries_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'code',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'total_holidays',
  'type': 'integer',
  'nullable': False,
  'default': '0'},
 {'name': 'weekend_start',
  'type': 'integer',
  'nullable': False,
  'default': '6'},
 {'name': 'weekend_end', 'type': 'integer', 'nullable': False, 'default': '7'}]

In [11]:
country_df = pd.read_csv(CSV_PATH + "country.csv")
country_df.head()

id code                  name  total_holidays  weekend_start  weekend_end
0   1   AD               Andorra              28              6            7
1   2   AE  United Arab Emirates              23              6            7
2   3   AF           Afghanistan              24              5            6
3   4   AG   Antigua and Barbuda              15              6            7
4   5   AI              Anguilla              19              6            7

In [12]:
country_df[country_df["code"].isna()]

id code     name  total_holidays  weekend_start  weekend_end
147  148  NaN  Namibia              18              6            7

In [13]:
country_df.at[147, "code"] = "NA"
assert len(country_df[country_df["code"].isna()]) == 0
assert country_df["code"].nunique() == len(country_df)

In [14]:
if "id" in country_df.columns:
    country_df.drop(columns=["id"], inplace=True)

data = country_df.to_dict('records')
assert len(data) == len(country_df)

data

[{'code': 'AD',
  'name': 'Andorra',
  'total_holidays': 28,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AE',
  'name': 'United Arab Emirates',
  'total_holidays': 23,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AF',
  'name': 'Afghanistan',
  'total_holidays': 24,
  'weekend_start': 5,
  'weekend_end': 6},
 {'code': 'AG',
  'name': 'Antigua and Barbuda',
  'total_holidays': 15,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AI',
  'name': 'Anguilla',
  'total_holidays': 19,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AL',
  'name': 'Albania',
  'total_holidays': 33,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AM',
  'name': 'Armenia',
  'total_holidays': 37,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AO',
  'name': 'Angola',
  'total_holidays': 18,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AR',
  'name': 'Argentina',
  'total_holidays': 41,
  'weekend_start': 6,
  'weekend_end': 7},
 {'code': 'AS',
  'name': 'Americ

In [15]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 230 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AD',
   'name': 'Andorra',
   'total_holidays': 28,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 2,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AE',
   'name': 'United Arab Emirates',
   'total_holidays': 23,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 3,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AF',
   'name': 'Afghanistan',
   'total_holidays': 24,
   'weekend_start': 5,
   'weekend_end': 6},
  {'id': 4,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AG',
   'name': 'Antigua and Barbuda',
   'total_holidays': 15,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 5,
   'created_at': '2025-07-29T07:13:14.

In [16]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 230 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AD',
   'name': 'Andorra',
   'total_holidays': 28,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 2,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AE',
   'name': 'United Arab Emirates',
   'total_holidays': 23,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 3,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AF',
   'name': 'Afghanistan',
   'total_holidays': 24,
   'weekend_start': 5,
   'weekend_end': 6},
  {'id': 4,
   'created_at': '2025-07-29T07:13:14.419Z',
   'updated_at': '2025-07-29T07:13:14.419Z',
   'code': 'AG',
   'name': 'Antigua and Barbuda',
   'total_holidays': 15,
   'weekend_start': 6,
   'weekend_end': 7},
  {'id': 5,
   'created_at': '2025-07-29T07:13:14.419Z',
   'u

In [17]:
data = response['data']
assert len(data) == len(country_df)

### Locations

In [18]:
endpoint = "db/tables/locations"

In [19]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('locations_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'city',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'state',
  'type': 'character varying',
  'nullable': True,
  'default': None},
 {'name': 'country_code',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'latitude', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'longitude', 'type': 'numeric', 'nullable': False, 'default': None}]

In [20]:
location_df = pd.read_csv(CSV_PATH + "location.csv")
location_df.head()

id                               name        city              state  \
0   1                BALERNA, TICINO, CH     Balerna             Ticino   
1   2              BERGAMO, LOMBARDY, IT     Bergamo           Lombardy   
2   3            BOCA RATON, FLORIDA, US  Boca Raton            Florida   
3   4  BRATISLAVA, BRATISLAVA REGION, SK  Bratislava  Bratislava Region   
4   5              BRESCIA, LOMBARDY, IT     Brescia           Lombardy   

  country_code  latitude  longitude  
0           CH  45.84638    9.00724  
1           IT  45.69601    9.66721  
2           US  26.35869  -80.08310  
3           SK  48.14816   17.10674  
4           IT  45.53558   10.21472

In [21]:
assert len(location_df[location_df["name"].isna()]) == 0
assert location_df['name'].unique().size == len(location_df)

assert len(location_df[location_df["city"].isna()]) == 0
location_df['state'] = location_df['state'].where(pd.notnull(location_df["state"]), None)
assert len(location_df[location_df["country_code"].isna()]) == 0
assert len(location_df[location_df["latitude"].isna()]) == 0
assert len(location_df[location_df["longitude"].isna()]) == 0

assert len(location_df['name'].unique()) == len(location_df)
assert location_df['country_code'].isin(country_df['code'].values).all()

In [22]:
if "id" in location_df.columns:
    location_df.drop(columns=["id"], inplace=True)

data = location_df.to_dict('records')
assert len(data) == len(location_df)

data

[{'name': 'BALERNA, TICINO, CH',
  'city': 'Balerna',
  'state': 'Ticino',
  'country_code': 'CH',
  'latitude': 45.84638,
  'longitude': 9.00724},
 {'name': 'BERGAMO, LOMBARDY, IT',
  'city': 'Bergamo',
  'state': 'Lombardy',
  'country_code': 'IT',
  'latitude': 45.69601,
  'longitude': 9.66721},
 {'name': 'BOCA RATON, FLORIDA, US',
  'city': 'Boca Raton',
  'state': 'Florida',
  'country_code': 'US',
  'latitude': 26.35869,
  'longitude': -80.0831},
 {'name': 'BRATISLAVA, BRATISLAVA REGION, SK',
  'city': 'Bratislava',
  'state': 'Bratislava Region',
  'country_code': 'SK',
  'latitude': 48.14816,
  'longitude': 17.10674},
 {'name': 'BRESCIA, LOMBARDY, IT',
  'city': 'Brescia',
  'state': 'Lombardy',
  'country_code': 'IT',
  'latitude': 45.53558,
  'longitude': 10.21472},
 {'name': 'BRUSSELS, BRUSSELS CAPITAL, BE',
  'city': 'Brussels',
  'state': 'Brussels Capital',
  'country_code': 'BE',
  'latitude': 50.85045,
  'longitude': 4.34878},
 {'name': 'CASTLE DONINGTON, ENGLAND, GB',


In [23]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 45 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BALERNA, TICINO, CH',
   'city': 'Balerna',
   'state': 'Ticino',
   'country_code': 'CH',
   'latitude': '45.8463800',
   'longitude': '9.0072400'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BERGAMO, LOMBARDY, IT',
   'city': 'Bergamo',
   'state': 'Lombardy',
   'country_code': 'IT',
   'latitude': '45.6960100',
   'longitude': '9.6672100'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BOCA RATON, FLORIDA, US',
   'city': 'Boca Raton',
   'state': 'Florida',
   'country_code': 'US',
   'latitude': '26.3586900',
   'longitude': '-80.0831000'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BRAT

In [24]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 45 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BALERNA, TICINO, CH',
   'city': 'Balerna',
   'state': 'Ticino',
   'country_code': 'CH',
   'latitude': '45.8463800',
   'longitude': '9.0072400'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BERGAMO, LOMBARDY, IT',
   'city': 'Bergamo',
   'state': 'Lombardy',
   'country_code': 'IT',
   'latitude': '45.6960100',
   'longitude': '9.6672100'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BOCA RATON, FLORIDA, US',
   'city': 'Boca Raton',
   'state': 'Florida',
   'country_code': 'US',
   'latitude': '26.3586900',
   'longitude': '-80.0831000'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:16.706Z',
   'updated_at': '2025-07-29T07:13:16.706Z',
   'name': 'BRATISLAVA, BRAT

In [25]:
data = response['data']
assert len(data) == len(location_df)

### Carriers

In [26]:
endpoint = "db/tables/carriers"

In [27]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('carriers_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'carrier_17track_id',
  'type': 'character varying',
  'nullable': True,
  'default': None},
 {'name': 'n_losses', 'type': 'integer', 'nullable': False, 'default': '0'},
 {'name': 'n_orders', 'type': 'integer', 'nullable': False, 'default': '0'}]

In [28]:
carriers_df = pd.read_csv(CSV_PATH + "carrier.csv")
carriers_df.head()

id         name  carrier_17track_id  n_losses  n_orders
0   1  DHL Express              100001         0         5
1   2          UPS              100002         0        72
2   3        FedEx              100003         0        13
3   4          DHL              100004         0        16
4   5          DPD              100005         0         0

In [29]:
assert len(carriers_df[carriers_df["name"].isna()]) == 0
assert carriers_df['name'].unique().size == len(carriers_df)
assert carriers_df['carrier_17track_id'].unique().size == len(carriers_df)
assert len(carriers_df[carriers_df["n_losses"] < 0]) == 0
assert len(carriers_df[carriers_df["n_orders"] < 0]) == 0

In [30]:
if "id" in carriers_df.columns:
    carriers_df.drop(columns=["id"], inplace=True)

data = carriers_df.to_dict('records')
assert len(data) == len(carriers_df)

data

[{'name': 'DHL Express',
  'carrier_17track_id': 100001,
  'n_losses': 0,
  'n_orders': 5},
 {'name': 'UPS', 'carrier_17track_id': 100002, 'n_losses': 0, 'n_orders': 72},
 {'name': 'FedEx',
  'carrier_17track_id': 100003,
  'n_losses': 0,
  'n_orders': 13},
 {'name': 'DHL', 'carrier_17track_id': 100004, 'n_losses': 0, 'n_orders': 16},
 {'name': 'DPD', 'carrier_17track_id': 100005, 'n_losses': 0, 'n_orders': 0},
 {'name': 'GLS', 'carrier_17track_id': 100006, 'n_losses': 0, 'n_orders': 0},
 {'name': 'Hermes',
  'carrier_17track_id': 100007,
  'n_losses': 0,
  'n_orders': 0},
 {'name': 'TNT', 'carrier_17track_id': 100008, 'n_losses': 0, 'n_orders': 0},
 {'name': 'Royal Mail',
  'carrier_17track_id': 100009,
  'n_losses': 0,
  'n_orders': 0},
 {'name': 'USPS', 'carrier_17track_id': 100010, 'n_losses': 0, 'n_orders': 0},
 {'name': 'Canada Post',
  'carrier_17track_id': 100011,
  'n_losses': 0,
  'n_orders': 0},
 {'name': 'Australia Post',
  'carrier_17track_id': 100012,
  'n_losses': 0,
  '

In [31]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 20 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DHL Express',
   'carrier_17track_id': '100001',
   'n_losses': 0,
   'n_orders': 5},
  {'id': 2,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'UPS',
   'carrier_17track_id': '100002',
   'n_losses': 0,
   'n_orders': 72},
  {'id': 3,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'FedEx',
   'carrier_17track_id': '100003',
   'n_losses': 0,
   'n_orders': 13},
  {'id': 4,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DHL',
   'carrier_17track_id': '100004',
   'n_losses': 0,
   'n_orders': 16},
  {'id': 5,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DPD',
   'carrier_17track_id'

In [32]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 20 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DHL Express',
   'carrier_17track_id': '100001',
   'n_losses': 0,
   'n_orders': 5},
  {'id': 2,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'UPS',
   'carrier_17track_id': '100002',
   'n_losses': 0,
   'n_orders': 72},
  {'id': 3,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'FedEx',
   'carrier_17track_id': '100003',
   'n_losses': 0,
   'n_orders': 13},
  {'id': 4,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DHL',
   'carrier_17track_id': '100004',
   'n_losses': 0,
   'n_orders': 16},
  {'id': 5,
   'created_at': '2025-07-29T07:13:18.199Z',
   'updated_at': '2025-07-29T07:13:18.199Z',
   'name': 'DPD',
   'carrier_17track_id': '100005',


In [33]:
data = response['data']
assert len(data) == len(carriers_df)

### Manufacturers

In [34]:
endpoint = "db/tables/manufacturers"

In [35]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('manufacturers_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'location_name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None}]

In [36]:
manufacturers_df = pd.read_csv(CSV_PATH + "manufacturer.csv")
manufacturers_df.head()

id            location_name name
0   1  GAZZANIGA, LOMBARDY, IT  FAE

In [37]:
assert len(manufacturers_df[manufacturers_df["location_name"].isna()]) == 0
assert len(manufacturers_df[manufacturers_df["name"].isna()]) == 0

In [38]:
#if "id" in manufacturers_df.columns:
#    manufacturers_df.drop(columns=["id"], inplace=True)

data = manufacturers_df.to_dict('records')
assert len(data) == len(manufacturers_df)

data

[{'id': 1, 'location_name': 'GAZZANIGA, LOMBARDY, IT', 'name': 'FAE'}]

In [39]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:19.486Z',
   'updated_at': '2025-07-29T07:13:19.486Z',
   'location_name': 'GAZZANIGA, LOMBARDY, IT',
   'name': 'FAE'}],
 'meta': {'recordsAffected': 1, 'executionTime': 259},
 'timestamp': '2025-07-29T07:13:19.499Z'}

In [40]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:19.486Z',
   'updated_at': '2025-07-29T07:13:19.486Z',
   'location_name': 'GAZZANIGA, LOMBARDY, IT',
   'name': 'FAE'}],
 'meta': {'recordsAffected': 1, 'executionTime': 224},
 'timestamp': '2025-07-29T07:13:19.821Z'}

In [41]:
data = response['data']
assert len(data) == len(manufacturers_df)

### Suppliers

In [42]:
endpoint = "db/tables/suppliers"

In [43]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('suppliers_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'manufacturer_supplier_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None}]

In [44]:
suppliers_df = pd.read_csv(CSV_PATH + "supplier.csv")
suppliers_df.head()

id  manufacturer_supplier_id         name
0   1                         1      FARNELL
1   2                         2      DIGIKEY
2   3                         3       MOUSER
3   4                         4  AUTO SUPPLY
4   5                         8         SAFE

In [45]:
assert len(suppliers_df[suppliers_df["manufacturer_supplier_id"].isna()]) == 0
assert len(suppliers_df[suppliers_df["name"].isna()]) == 0

In [46]:
#if "id" in suppliers_df.columns:
#    suppliers_df.drop(columns=["id"], inplace=True)        

data = suppliers_df.to_dict('records')
assert len(data) == len(suppliers_df)

data

[{'id': 1, 'manufacturer_supplier_id': 1, 'name': 'FARNELL'},
 {'id': 2, 'manufacturer_supplier_id': 2, 'name': 'DIGIKEY'},
 {'id': 3, 'manufacturer_supplier_id': 3, 'name': 'MOUSER'},
 {'id': 4, 'manufacturer_supplier_id': 4, 'name': 'AUTO SUPPLY'},
 {'id': 5, 'manufacturer_supplier_id': 8, 'name': 'SAFE'},
 {'id': 6, 'manufacturer_supplier_id': 9, 'name': 'WURTH'},
 {'id': 7, 'manufacturer_supplier_id': 10, 'name': 'LCSC'},
 {'id': 8, 'manufacturer_supplier_id': 14, 'name': 'TME'},
 {'id': 9, 'manufacturer_supplier_id': 28, 'name': 'SAMTEC'},
 {'id': 10, 'manufacturer_supplier_id': 49, 'name': 'NCAB'},
 {'id': 11, 'manufacturer_supplier_id': 50, 'name': 'WINSOURCE'},
 {'id': 12, 'manufacturer_supplier_id': 150, 'name': 'AMALFI'},
 {'id': 13, 'manufacturer_supplier_id': 349, 'name': 'WIN SOURCE'},
 {'id': 14, 'manufacturer_supplier_id': 401, 'name': 'UNKNOWN1'},
 {'id': 15, 'manufacturer_supplier_id': 436, 'name': 'UNKNOWN2'},
 {'id': 16, 'manufacturer_supplier_id': 453, 'name': 'UNKN

In [47]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 16 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 1,
   'name': 'FARNELL'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 2,
   'name': 'DIGIKEY'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 3,
   'name': 'MOUSER'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 4,
   'name': 'AUTO SUPPLY'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 8,
   'name': 'SAFE'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_i

In [48]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 16 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 1,
   'name': 'FARNELL'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 2,
   'name': 'DIGIKEY'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 3,
   'name': 'MOUSER'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 4,
   'name': 'AUTO SUPPLY'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 8,
   'name': 'SAFE'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:20.819Z',
   'updated_at': '2025-07-29T07:13:20.819Z',
   'manufacturer_supplier_id': 9,
   'n

In [49]:
data = response['data']
assert len(data) == len(suppliers_df)

### Sites

In [50]:
endpoint = "db/tables/sites"

In [51]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('sites_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'supplier_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'location_name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'n_rejections',
  'type': 'integer',
  'nullable': False,
  'default': '0'},
 {'name': 'n_orders', 'type': 'integer', 'nullable': False, 'default': '0'},
 {'name': 'consider_closure_holidays',
  'type': 'boolean',
  'nullable': False,
  'default': 'true'},
 {'name': 'consider_working_holidays',
  'type': 'boolean',
  'nullable': False,
  'default': 'true'},
 {'name': 'consider_weekends_holidays',
  'type': 'boolean',
  'nullable': False,
  'default': 'tru

In [52]:
sites_df = pd.read_csv(CSV_PATH + "site.csv")
sites_df.head()

id  supplier_id                     location_name  n_rejections  n_orders  \
0   1            1                LEEDS, ENGLAND, GB             0         5   
1   2            2          LOUISVILLE, KENTUCKY, US             0         3   
2   3            2  THIEF RIVER FALLS, MINNESOTA, US             0        61   
3   4            3          GRAND PRAIRIE, TEXAS, US             0         5   
4   5            4            MONTAGNOLA, TICINO, CH             0         1   

   consider_closure_holidays  consider_working_holidays  \
0                       True                       True   
1                       True                       True   
2                       True                       True   
3                       True                       True   
4                       True                       True   

   consider_weekends_holidays  
0                        True  
1                        True  
2                        True  
3                        True  
4                        True

In [53]:
assert len(sites_df[sites_df["supplier_id"].isna()]) == 0
assert len(sites_df[sites_df["location_name"].isna()]) == 0
assert len(sites_df[sites_df["n_rejections"] < 0]) == 0
assert len(sites_df[sites_df["n_orders"] <= 0]) == 0

In [54]:
#if "id" in sites_df.columns:
#    sites_df.drop(columns=["id"], inplace=True)

data = sites_df.to_dict('records')
assert len(data) == len(sites_df)

data

[{'id': 1,
  'supplier_id': 1,
  'location_name': 'LEEDS, ENGLAND, GB',
  'n_rejections': 0,
  'n_orders': 5,
  'consider_closure_holidays': True,
  'consider_working_holidays': True,
  'consider_weekends_holidays': True},
 {'id': 2,
  'supplier_id': 2,
  'location_name': 'LOUISVILLE, KENTUCKY, US',
  'n_rejections': 0,
  'n_orders': 3,
  'consider_closure_holidays': True,
  'consider_working_holidays': True,
  'consider_weekends_holidays': True},
 {'id': 3,
  'supplier_id': 2,
  'location_name': 'THIEF RIVER FALLS, MINNESOTA, US',
  'n_rejections': 0,
  'n_orders': 61,
  'consider_closure_holidays': True,
  'consider_working_holidays': True,
  'consider_weekends_holidays': True},
 {'id': 4,
  'supplier_id': 3,
  'location_name': 'GRAND PRAIRIE, TEXAS, US',
  'n_rejections': 0,
  'n_orders': 5,
  'consider_closure_holidays': True,
  'consider_working_holidays': True,
  'consider_weekends_holidays': True},
 {'id': 5,
  'supplier_id': 4,
  'location_name': 'MONTAGNOLA, TICINO, CH',
  'n_

In [55]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 21 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 1,
   'location_name': 'LEEDS, ENGLAND, GB',
   'n_rejections': 0,
   'n_orders': 5,
   'consider_closure_holidays': True,
   'consider_working_holidays': True,
   'consider_weekends_holidays': True},
  {'id': 2,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 2,
   'location_name': 'LOUISVILLE, KENTUCKY, US',
   'n_rejections': 0,
   'n_orders': 3,
   'consider_closure_holidays': True,
   'consider_working_holidays': True,
   'consider_weekends_holidays': True},
  {'id': 3,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 2,
   'location_name': 'THIEF RIVER FALLS, MINNESOTA, US',
   'n_rejections': 0,
   'n_orders': 61,
   'consider_closure_holidays': True,
   'consider_worki

In [56]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 21 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 1,
   'location_name': 'LEEDS, ENGLAND, GB',
   'n_rejections': 0,
   'n_orders': 5,
   'consider_closure_holidays': True,
   'consider_working_holidays': True,
   'consider_weekends_holidays': True},
  {'id': 2,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 2,
   'location_name': 'LOUISVILLE, KENTUCKY, US',
   'n_rejections': 0,
   'n_orders': 3,
   'consider_closure_holidays': True,
   'consider_working_holidays': True,
   'consider_weekends_holidays': True},
  {'id': 3,
   'created_at': '2025-07-29T07:13:22.549Z',
   'updated_at': '2025-07-29T07:13:22.549Z',
   'supplier_id': 2,
   'location_name': 'THIEF RIVER FALLS, MINNESOTA, US',
   'n_rejections': 0,
   'n_orders': 61,
   'consider_closure_holidays': True,
   'consider_working_holidays'

In [57]:
data = response['data']
assert len(data) == len(sites_df)

### Orders

In [58]:
endpoint = "db/tables/orders"

In [59]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('orders_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'manufacturer_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'manufacturer_order_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'carrier_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'status',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'sub_status',
  'type': 'character varying',
  'nullable': True,
  'default': None},
 {'name': 'exception_details',
  'type': 'text',
  'nullable': True,
  'default': None},
 {'name': 'completion_type',
  't

In [60]:
orders_df = pd.read_csv(CSV_PATH + "order_train.csv")
orders_df.head()

id  manufacturer_id  manufacturer_order_id  site_id  carrier_id     status  \
0   1                1                   6004        8           1  DELIVERED   
1   2                1                   6005        1           2  DELIVERED   
2   3                1                   6037        3           2  DELIVERED   
3   4                1                   6045        3           2  DELIVERED   
4   5                1                   6046        4           3  DELIVERED   

   n_steps                                      tracking_link  \
0       14  https://mydhl.express.dhl/it/it/tracking.html#...   
1       11                                 1Z60699Y0400391867   
2       11                                 1ZR465910413218509   
3       12  https://www.digikey.it/OrderHistory/shipmenttr...   
4       14  https://www.fedex.com/fedextrack/?trknbr=43744...   

      tracking_number manufacturer_creation_timestamp  \
0          1656325344       2025-01-07 07:31:00+00:00   
1  1Z60699Y0400391867       2025-01-07 13:57:00+00:00   
2  1ZR465910413218509       2025-01-10 13:41:00+00:00   
3  1ZR465910413219320       2025-01-13 15:27:00+00:00   
4        437446419489       2025-01-13 15:27:00+00:00   

  manufacturer_estimated_delivery_timestamp  \
0                 2025-01-13 22:00:00+00:00   
1                 2025-01-08 22:00:00+00:00   
2                 2025-01-14 22:00:00+00:00   
3                 2025-01-15 22:00:00+00:00   
4                 2025-01-15 22:00:00+00:00   

  manufacturer_confirmed_delivery_timestamp carrier_creation_timestamp  \
0                 2025-01-17 11:36:00+00:00  2025-01-14 09:16:00+00:00   
1                 2025-01-13 12:47:00+00:00  2025-01-09 03:11:00+00:00   
2                 2025-01-15 09:18:00+00:00  2025-01-11 00:10:00+00:00   
3                 2025-01-15 09:45:00+00:00  2025-01-13 17:08:00+00:00   
4                 2025-01-15 12:14:00+00:00  2025-01-13 20:15:00+00:00   

   carrier_estimated_delivery_timestamp carrier_confirmed_delivery_timestamp  \
0                                   NaN            2025-01-17 10:40:00+00:00   
1                                   NaN            2025-01-13 09:19:00+00:00   
2                                   NaN            2025-01-15 09:47:00+00:00   
3                                   NaN            2025-01-15 09:47:00+00:00   
4                                   NaN            2025-01-15 11:49:00+00:00   

   SLS  SRS  
0    0    0  
1    0    0  
2    0    0  
3    0    0  
4    0    0

In [61]:
from datetime import timezone

def is_utc(dt: datetime) -> bool:
    return dt.tzinfo is not None and dt.tzinfo.utcoffset(dt) == timezone.utc.utcoffset(None)

In [62]:
assert len(orders_df[orders_df["manufacturer_id"].isna()]) == 0
assert len(orders_df[orders_df["manufacturer_order_id"].isna()]) == 0
assert len(orders_df[orders_df["site_id"].isna()]) == 0
assert len(orders_df[orders_df["carrier_id"].isna()]) == 0
assert len(orders_df[orders_df["status"].isna()]) == 0
assert len(orders_df[orders_df["n_steps"] <= 0]) == 0
assert len(orders_df[orders_df["tracking_link"].isna()]) == 0
assert len(orders_df[orders_df["manufacturer_creation_timestamp"].isna()]) == 0

orders_df["manufacturer_creation_timestamp"] = pd.to_datetime(orders_df["manufacturer_creation_timestamp"], utc=True)
assert all(orders_df["manufacturer_creation_timestamp"].apply(is_utc))
orders_df["carrier_creation_timestamp"] = pd.to_datetime(orders_df["carrier_creation_timestamp"], utc=True)
assert all(orders_df["carrier_creation_timestamp"].apply(is_utc))
orders_df["carrier_confirmed_delivery_timestamp"] = pd.to_datetime(orders_df["carrier_confirmed_delivery_timestamp"], utc=True)
assert all(orders_df["carrier_confirmed_delivery_timestamp"].apply(is_utc))

for col in [
    "manufacturer_estimated_delivery_timestamp", 
    "manufacturer_confirmed_delivery_timestamp",
    "carrier_creation_timestamp", 
    "carrier_estimated_delivery_timestamp", 
    "carrier_confirmed_delivery_timestamp"
]:
    orders_df[col] = orders_df[col].astype("object").where(pd.notnull(orders_df[col]), None)

orders_df['manufacturer_creation_timestamp'] = orders_df['manufacturer_creation_timestamp'].apply(lambda x: x.isoformat()) 
orders_df['carrier_creation_timestamp'] = orders_df['carrier_creation_timestamp'].apply(lambda x: x.isoformat())
orders_df['carrier_confirmed_delivery_timestamp'] = orders_df['carrier_confirmed_delivery_timestamp'].apply(lambda x: x.isoformat())

assert len(orders_df[orders_df["SLS"].isna()]) == 0

In [63]:
#if "id" in sites_df.columns:
#    sites_df.drop(columns=["id"], inplace=True)

data = orders_df.to_dict('records')
assert len(data) == len(orders_df)

data

[{'id': 1,
  'manufacturer_id': 1,
  'manufacturer_order_id': 6004,
  'site_id': 8,
  'carrier_id': 1,
  'status': 'DELIVERED',
  'n_steps': 14,
  'tracking_link': 'https://mydhl.express.dhl/it/it/tracking.html#/results?id=1656325344',
  'tracking_number': '1656325344',
  'manufacturer_creation_timestamp': '2025-01-07T07:31:00+00:00',
  'manufacturer_estimated_delivery_timestamp': '2025-01-13 22:00:00+00:00',
  'manufacturer_confirmed_delivery_timestamp': '2025-01-17 11:36:00+00:00',
  'carrier_creation_timestamp': '2025-01-14T09:16:00+00:00',
  'carrier_estimated_delivery_timestamp': None,
  'carrier_confirmed_delivery_timestamp': '2025-01-17T10:40:00+00:00',
  'SLS': 0,
  'SRS': 0},
 {'id': 2,
  'manufacturer_id': 1,
  'manufacturer_order_id': 6005,
  'site_id': 1,
  'carrier_id': 2,
  'status': 'DELIVERED',
  'n_steps': 11,
  'tracking_link': '1Z60699Y0400391867',
  'tracking_number': '1Z60699Y0400391867',
  'manufacturer_creation_timestamp': '2025-01-07T13:57:00+00:00',
  'manufact

In [64]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 88 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:24.719Z',
   'updated_at': '2025-07-29T07:13:24.719Z',
   'manufacturer_id': 1,
   'manufacturer_order_id': 6004,
   'site_id': 8,
   'carrier_id': 1,
   'status': 'DELIVERED',
   'sub_status': None,
   'exception_details': None,
   'completion_type': None,
   'n_steps': 14,
   'tracking_link': 'https://mydhl.express.dhl/it/it/tracking.html#/results?id=1656325344',
   'tracking_number': '1656325344',
   'manufacturer_creation_timestamp': '2025-01-07T07:31:00.000Z',
   'manufacturer_estimated_delivery_timestamp': '2025-01-13T22:00:00.000Z',
   'manufacturer_confirmed_delivery_timestamp': '2025-01-17T11:36:00.000Z',
   'carrier_creation_timestamp': '2025-01-14T09:16:00.000Z',
   'carrier_estimated_delivery_timestamp': None,
   'carrier_confirmed_delivery_timestamp': '2025-01-17T10:40:00.000Z',
   'SLS': False,
   'SRS': False},
  {'id': 2,
   'created_at': '2025-07-2

In [65]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 88 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:24.719Z',
   'updated_at': '2025-07-29T07:13:24.719Z',
   'manufacturer_id': 1,
   'manufacturer_order_id': 6004,
   'site_id': 8,
   'carrier_id': 1,
   'status': 'DELIVERED',
   'sub_status': None,
   'exception_details': None,
   'completion_type': None,
   'n_steps': 14,
   'tracking_link': 'https://mydhl.express.dhl/it/it/tracking.html#/results?id=1656325344',
   'tracking_number': '1656325344',
   'manufacturer_creation_timestamp': '2025-01-07T07:31:00.000Z',
   'manufacturer_estimated_delivery_timestamp': '2025-01-13T22:00:00.000Z',
   'manufacturer_confirmed_delivery_timestamp': '2025-01-17T11:36:00.000Z',
   'carrier_creation_timestamp': '2025-01-14T09:16:00.000Z',
   'carrier_estimated_delivery_timestamp': None,
   'carrier_confirmed_delivery_timestamp': '2025-01-17T10:40:00.000Z',
   'SLS': False,
   'SRS': False},
  {'id': 2,
   'created_at': '2025-07-29T07:13:24.7

In [66]:
data = response['data']
assert len(data) == len(orders_df)

### Vertices

In [67]:
endpoint = "db/tables/vertices"

In [68]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('vertices_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'type', 'type': 'text', 'nullable': False, 'default': None}]

In [69]:
vertices_df = pd.read_csv(CSV_PATH + "vertex.csv")
vertices_df.head()

id                    name           type
0   1     WARSAW, MAZOVIA, PL   INTERMEDIATE
1   2                       3  SUPPLIER_SITE
2   3    CINCINNATI, OHIO, US   INTERMEDIATE
3   4  ISTANBUL, ISTANBUL, TR   INTERMEDIATE
4   5                       8  SUPPLIER_SITE

In [70]:
assert len(vertices_df[vertices_df["id"].isna()]) == 0
assert len(vertices_df[vertices_df["name"].isna()]) == 0
assert len(vertices_df[vertices_df["type"].isna()]) == 0

In [71]:
#if "id" in sites_df.columns:
#    sites_df.drop(columns=["id"], inplace=True)

data = vertices_df.to_dict('records')
assert len(data) == len(vertices_df)

data

[{'id': 1, 'name': 'WARSAW, MAZOVIA, PL', 'type': 'INTERMEDIATE'},
 {'id': 2, 'name': '3', 'type': 'SUPPLIER_SITE'},
 {'id': 3, 'name': 'CINCINNATI, OHIO, US', 'type': 'INTERMEDIATE'},
 {'id': 4, 'name': 'ISTANBUL, ISTANBUL, TR', 'type': 'INTERMEDIATE'},
 {'id': 5, 'name': '8', 'type': 'SUPPLIER_SITE'},
 {'id': 6, 'name': 'BOCA RATON, FLORIDA, US', 'type': 'INTERMEDIATE'},
 {'id': 7,
  'name': 'COLOGNE, NORTH RHINE-WESTPHALIA, DE',
  'type': 'INTERMEDIATE'},
 {'id': 8, 'name': '5', 'type': 'SUPPLIER_SITE'},
 {'id': 9, 'name': 'BALERNA, TICINO, CH', 'type': 'INTERMEDIATE'},
 {'id': 10, 'name': '7', 'type': 'SUPPLIER_SITE'},
 {'id': 11, 'name': '11', 'type': 'SUPPLIER_SITE'},
 {'id': 12, 'name': 'NEW DELHI, DELHI, IN', 'type': 'INTERMEDIATE'},
 {'id': 13, 'name': '13', 'type': 'SUPPLIER_SITE'},
 {'id': 14, 'name': '15', 'type': 'SUPPLIER_SITE'},
 {'id': 15,
  'name': 'BRATISLAVA, BRATISLAVA REGION, SK',
  'type': 'INTERMEDIATE'},
 {'id': 16, 'name': 'MINNEAPOLIS, MINNESOTA, US', 'type': 

In [72]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 66 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'WARSAW, MAZOVIA, PL',
   'type': 'INTERMEDIATE'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': '3',
   'type': 'SUPPLIER_SITE'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'CINCINNATI, OHIO, US',
   'type': 'INTERMEDIATE'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'ISTANBUL, ISTANBUL, TR',
   'type': 'INTERMEDIATE'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': '8',
   'type': 'SUPPLIER_SITE'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'BOCA RATON, FLORIDA,

In [73]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 66 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'WARSAW, MAZOVIA, PL',
   'type': 'INTERMEDIATE'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': '3',
   'type': 'SUPPLIER_SITE'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'CINCINNATI, OHIO, US',
   'type': 'INTERMEDIATE'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'ISTANBUL, ISTANBUL, TR',
   'type': 'INTERMEDIATE'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': '8',
   'type': 'SUPPLIER_SITE'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:26.341Z',
   'updated_at': '2025-07-29T07:13:26.341Z',
   'name': 'BOCA RATON, FLORIDA, US',
   'ty

In [74]:
data = response['data']
assert len(data) == len(vertices_df)

### Routes

In [75]:
endpoint = "db/tables/routes"

In [76]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('routes_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'source_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'destination_id',
  'type': 'integer',
  'nullable': False,
  'default': None}]

In [77]:
routes_df = pd.read_csv(CSV_PATH + "route.csv")
routes_df.head()

source_id  destination_id
0         57              48
1         31              47
2         32              12
3         51              25
4         59              39

In [78]:
assert len(routes_df[routes_df["source_id"].isna()]) == 0
assert len(routes_df[routes_df["destination_id"].isna()]) == 0

In [79]:
#if "id" in sites_df.columns:
#    sites_df.drop(columns=["id"], inplace=True)

data = routes_df.to_dict('records')
assert len(data) == len(routes_df)

data

[{'source_id': 57, 'destination_id': 48},
 {'source_id': 31, 'destination_id': 47},
 {'source_id': 32, 'destination_id': 12},
 {'source_id': 51, 'destination_id': 25},
 {'source_id': 59, 'destination_id': 39},
 {'source_id': 31, 'destination_id': 65},
 {'source_id': 7, 'destination_id': 19},
 {'source_id': 14, 'destination_id': 15},
 {'source_id': 11, 'destination_id': 62},
 {'source_id': 25, 'destination_id': 61},
 {'source_id': 35, 'destination_id': 1},
 {'source_id': 66, 'destination_id': 25},
 {'source_id': 24, 'destination_id': 19},
 {'source_id': 36, 'destination_id': 48},
 {'source_id': 49, 'destination_id': 39},
 {'source_id': 21, 'destination_id': 41},
 {'source_id': 52, 'destination_id': 19},
 {'source_id': 50, 'destination_id': 40},
 {'source_id': 1, 'destination_id': 19},
 {'source_id': 4, 'destination_id': 61},
 {'source_id': 7, 'destination_id': 23},
 {'source_id': 56, 'destination_id': 7},
 {'source_id': 48, 'destination_id': 24},
 {'source_id': 45, 'destination_id': 16}

In [80]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 82 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 57,
   'destination_id': 48},
  {'id': 2,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 31,
   'destination_id': 47},
  {'id': 3,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 32,
   'destination_id': 12},
  {'id': 4,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 51,
   'destination_id': 25},
  {'id': 5,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 59,
   'destination_id': 39},
  {'id': 6,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 31,
   'destination_id': 65},
  {'id': 7,
   'created_at': '2025-0

In [81]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 82 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 57,
   'destination_id': 48},
  {'id': 2,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 31,
   'destination_id': 47},
  {'id': 3,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 32,
   'destination_id': 12},
  {'id': 4,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 51,
   'destination_id': 25},
  {'id': 5,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 59,
   'destination_id': 39},
  {'id': 6,
   'created_at': '2025-07-29T07:13:27.966Z',
   'updated_at': '2025-07-29T07:13:27.966Z',
   'source_id': 31,
   'destination_id': 65},
  {'id': 7,
   'created_at': '2025-07-29T07:13:2

In [82]:
data = response['data']
assert len(data) == len(routes_df)

### Route_orders

In [83]:
endpoint = "db/tables/route_orders"

In [84]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('route_orders_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'source_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'destination_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'order_id', 'type': 'integer', 'nullable': False, 'default': None}]

In [85]:
route_orders_df = pd.read_csv(CSV_PATH + "route_order.csv")
route_orders_df.head()

source_id  destination_id  order_id
0          7              23        45
1         13              57        19
2         37              56        52
3         23              60       102
4         19              40        39

In [86]:
assert len(route_orders_df[route_orders_df["source_id"].isna()]) == 0
assert len(route_orders_df[route_orders_df["destination_id"].isna()]) == 0
assert len(route_orders_df[route_orders_df["order_id"].isna()]) == 0

In [87]:
#if "id" in sites_df.columns:
#    sites_df.drop(columns=["id"], inplace=True)

data = route_orders_df.to_dict('records')
assert len(data) == len(route_orders_df)

data

[{'source_id': 7, 'destination_id': 23, 'order_id': 45},
 {'source_id': 13, 'destination_id': 57, 'order_id': 19},
 {'source_id': 37, 'destination_id': 56, 'order_id': 52},
 {'source_id': 23, 'destination_id': 60, 'order_id': 102},
 {'source_id': 19, 'destination_id': 40, 'order_id': 39},
 {'source_id': 14, 'destination_id': 15, 'order_id': 11},
 {'source_id': 56, 'destination_id': 7, 'order_id': 67},
 {'source_id': 60, 'destination_id': 34, 'order_id': 31},
 {'source_id': 56, 'destination_id': 7, 'order_id': 76},
 {'source_id': 45, 'destination_id': 16, 'order_id': 35},
 {'source_id': 56, 'destination_id': 7, 'order_id': 85},
 {'source_id': 63, 'destination_id': 32, 'order_id': 26},
 {'source_id': 60, 'destination_id': 34, 'order_id': 49},
 {'source_id': 56, 'destination_id': 7, 'order_id': 94},
 {'source_id': 2, 'destination_id': 37, 'order_id': 29},
 {'source_id': 2, 'destination_id': 37, 'order_id': 38},
 {'source_id': 7, 'destination_id': 23, 'order_id': 4},
 {'source_id': 2, 'des

In [88]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 562 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 7,
   'destination_id': 23,
   'order_id': 45},
  {'id': 2,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 13,
   'destination_id': 57,
   'order_id': 19},
  {'id': 3,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 37,
   'destination_id': 56,
   'order_id': 52},
  {'id': 4,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 23,
   'destination_id': 60,
   'order_id': 102},
  {'id': 5,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 19,
   'destination_id': 40,
   'order_id': 39},
  {'id': 6,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07

In [89]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 562 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 7,
   'destination_id': 23,
   'order_id': 45},
  {'id': 2,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 13,
   'destination_id': 57,
   'order_id': 19},
  {'id': 3,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 37,
   'destination_id': 56,
   'order_id': 52},
  {'id': 4,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 23,
   'destination_id': 60,
   'order_id': 102},
  {'id': 5,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z',
   'source_id': 19,
   'destination_id': 40,
   'order_id': 39},
  {'id': 6,
   'created_at': '2025-07-29T07:13:29.599Z',
   'updated_at': '2025-07-29T07:13:29.599Z'

In [90]:
data = response['data']
assert len(data) == len(route_orders_df)

### Dispatch_times

In [91]:
endpoint = "db/tables/dispatch_times"

In [92]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('dispatch_times_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'hours', 'type': 'numeric', 'nullable': False, 'default': None}]

In [93]:
dispatch_times_df = pd.read_csv(CSV_PATH + "dispatch_time.csv")
dispatch_times_df.head()

id  site_id                 created_at       hours
0   1        8  2025-01-07 07:31:00+00:00  145.750000
1   2        1  2025-01-07 13:57:00+00:00   13.233333
2   3        3  2025-01-10 13:41:00+00:00   10.483333
3   4        3  2025-01-13 15:27:00+00:00    1.683333
4   5        4  2025-01-13 15:27:00+00:00    4.800000

In [94]:
assert not dispatch_times_df.isna().any().any()

In [95]:
if "id" in dispatch_times_df.columns:
    dispatch_times_df.drop(columns=["id"], inplace=True)

data = dispatch_times_df.to_dict('records')
assert len(data) == len(dispatch_times_df)

data

[{'site_id': 8, 'created_at': '2025-01-07 07:31:00+00:00', 'hours': 145.75},
 {'site_id': 1,
  'created_at': '2025-01-07 13:57:00+00:00',
  'hours': 13.233333333333334},
 {'site_id': 3,
  'created_at': '2025-01-10 13:41:00+00:00',
  'hours': 10.483333333333333},
 {'site_id': 3,
  'created_at': '2025-01-13 15:27:00+00:00',
  'hours': 1.6833333333333331},
 {'site_id': 4, 'created_at': '2025-01-13 15:27:00+00:00', 'hours': 4.8},
 {'site_id': 1, 'created_at': '2025-01-13 15:27:00+00:00', 'hours': 3.8},
 {'site_id': 3, 'created_at': '2025-01-15 14:44:00+00:00', 'hours': 23.0},
 {'site_id': 4,
  'created_at': '2025-01-20 16:45:00+00:00',
  'hours': 10.049999999999995},
 {'site_id': 1, 'created_at': '2025-01-21 14:31:00+00:00', 'hours': 4.25},
 {'site_id': 3, 'created_at': '2025-01-21 14:31:00+00:00', 'hours': 1.2},
 {'site_id': 15,
  'created_at': '2025-01-23 13:15:00+00:00',
  'hours': 170.43333333333334},
 {'site_id': 16,
  'created_at': '2025-01-27 09:47:00+00:00',
  'hours': 151.76666666

In [96]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 86 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 8,
   'hours': '145.750000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 1,
   'hours': '13.233333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 3,
   'hours': '10.483333'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 3,
   'hours': '1.683333'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 4,
   'hours': '4.800000'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 1,
   'hours': '3.800000'},
  {'id': 7,
   'created_at': '2025-07-29T07:13:31.741Z',

In [97]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 86 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 8,
   'hours': '145.750000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 1,
   'hours': '13.233333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 3,
   'hours': '10.483333'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 3,
   'hours': '1.683333'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 4,
   'hours': '4.800000'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated_at': '2025-07-29T07:13:31.741Z',
   'site_id': 1,
   'hours': '3.800000'},
  {'id': 7,
   'created_at': '2025-07-29T07:13:31.741Z',
   'updated

In [98]:
data = response['data']
assert len(data) == len(dispatch_times_df)

### Dispatch_time_samples

In [99]:
endpoint = "db/tables/dispatch_time_samples"

In [100]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('dispatch_time_samples_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'median', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'mean', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'std_dev', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'n', 'type': 'integer', 'nullable': False, 'default': None}]

In [101]:
dispatch_time_samples_df = pd.read_csv(CSV_PATH + "dispatch_time_sample.csv")
dispatch_time_samples_df.head()

id  site_id              created_at     median       mean    std_dev  n
0   1        1  2025-07-26T09:48+00:00   4.025000   5.783333   4.394836  4
1   2        2  2025-07-26T09:48+00:00  20.216667  20.288889   0.485786  3
2   3        4  2025-07-26T09:48+00:00  10.275000  19.316667  18.954540  4
3   4        5  2025-07-26T09:48+00:00   2.983333   2.983333   0.000000  1
4   5        6  2025-07-26T09:48+00:00  55.750000  52.050000  28.520727  3

In [102]:
assert not dispatch_time_samples_df.isna().any().any()

In [103]:
if "id" in dispatch_time_samples_df.columns:
    dispatch_time_samples_df.drop(columns=["id"], inplace=True)

data = dispatch_time_samples_df.to_dict('records')
assert len(data) == len(dispatch_time_samples_df)

data

[{'site_id': 1,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 4.025,
  'mean': 5.783333333333334,
  'std_dev': 4.394835984804591,
  'n': 4},
 {'site_id': 2,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 20.216666666666665,
  'mean': 20.288888888888888,
  'std_dev': 0.4857856053044248,
  'n': 3},
 {'site_id': 4,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 10.275,
  'mean': 19.316666666666663,
  'std_dev': 18.954539913522915,
  'n': 4},
 {'site_id': 5,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 2.9833333333333334,
  'mean': 2.9833333333333334,
  'std_dev': 0.0,
  'n': 1},
 {'site_id': 6,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 55.75,
  'mean': 52.04999999999999,
  'std_dev': 28.520726706236843,
  'n': 3},
 {'site_id': 7,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 22.0,
  'mean': 22.0,
  'std_dev': 0.0,
  'n': 1},
 {'site_id': 8,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 122.01666666666668,
  'mean': 122.01666666666

In [104]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 20 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 1,
   'median': '4.025000',
   'mean': '5.783333',
   'std_dev': '4.394836',
   'n': 4},
  {'id': 2,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 2,
   'median': '20.216667',
   'mean': '20.288889',
   'std_dev': '0.485786',
   'n': 3},
  {'id': 3,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 4,
   'median': '10.275000',
   'mean': '19.316667',
   'std_dev': '18.954540',
   'n': 4},
  {'id': 4,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 5,
   'median': '2.983333',
   'mean': '2.983333',
   'std_dev': '0.000000',
   'n': 1},
  {'id': 5,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z

In [105]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 20 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 1,
   'median': '4.025000',
   'mean': '5.783333',
   'std_dev': '4.394836',
   'n': 4},
  {'id': 2,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 2,
   'median': '20.216667',
   'mean': '20.288889',
   'std_dev': '0.485786',
   'n': 3},
  {'id': 3,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 4,
   'median': '10.275000',
   'mean': '19.316667',
   'std_dev': '18.954540',
   'n': 4},
  {'id': 4,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_id': 5,
   'median': '2.983333',
   'mean': '2.983333',
   'std_dev': '0.000000',
   'n': 1},
  {'id': 5,
   'created_at': '2025-07-29T07:13:33.144Z',
   'updated_at': '2025-07-29T07:13:33.144Z',
   'site_

In [106]:
data = response['data']
assert len(data) == len(dispatch_time_samples_df)

### Dispatch_time_gammas

In [107]:
endpoint = "db/tables/dispatch_time_gammas"

In [108]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('dispatch_time_gammas_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'shape', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'loc', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'scale', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'skewness', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'kurtosis', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'mean', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'std_dev', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'n', 'type': 'integer',

In [109]:
dispatch_time_gammas_df = pd.read_csv(CSV_PATH + "dispatch_time_gamma.csv")
dispatch_time_gammas_df.head()

id  site_id     shape  loc      scale  skewness  kurtosis  median  \
0   1        3  0.857671  1.2  28.363087  1.156895  0.197318  14.425   

        mean    std_dev   n  
0  26.154667  24.557424  50

In [110]:
assert not dispatch_time_gammas_df.isna().any().any()

In [111]:
if "id" in dispatch_time_gammas_df.columns:
    dispatch_time_gammas_df.drop(columns=["id"], inplace=True)

if "median" in dispatch_time_gammas_df.columns:
    dispatch_time_gammas_df.drop(columns=["median"], inplace=True)

data = dispatch_time_gammas_df.to_dict('records')
assert len(data) == len(dispatch_time_gammas_df)

data

[{'site_id': 3,
  'shape': 0.8576710969825438,
  'loc': 1.1999999999999995,
  'scale': 28.36308686245127,
  'skewness': 1.156894680158063,
  'kurtosis': 0.1973175696009161,
  'mean': 26.154666666666667,
  'std_dev': 24.55742403599056,
  'n': 50}]

In [112]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:34.659Z',
   'updated_at': '2025-07-29T07:13:34.659Z',
   'site_id': 3,
   'shape': '0.857671',
   'loc': '1.200000',
   'scale': '28.363087',
   'skewness': '1.156895',
   'kurtosis': '0.197318',
   'mean': '26.154667',
   'std_dev': '24.557424',
   'n': 50}],
 'meta': {'recordsAffected': 1, 'executionTime': 307},
 'timestamp': '2025-07-29T07:13:34.679Z'}

In [113]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:34.659Z',
   'updated_at': '2025-07-29T07:13:34.659Z',
   'site_id': 3,
   'shape': '0.857671',
   'loc': '1.200000',
   'scale': '28.363087',
   'skewness': '1.156895',
   'kurtosis': '0.197318',
   'mean': '26.154667',
   'std_dev': '24.557424',
   'n': 50}],
 'meta': {'recordsAffected': 1, 'executionTime': 209},
 'timestamp': '2025-07-29T07:13:35.062Z'}

In [114]:
data = response['data']
assert len(data) == len(dispatch_time_gammas_df)

### Shipment_times

In [115]:
endpoint = "db/tables/shipment_times"

In [116]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('shipment_times_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'carrier_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'hours', 'type': 'numeric', 'nullable': False, 'default': None}]

In [117]:
shipment_times_df = pd.read_csv(CSV_PATH + "shipment_time.csv")
shipment_times_df.head()

id  site_id  carrier_id                 created_at       hours
0   1        1           2  2025-01-13 09:19:00+00:00  102.133333
1   2        1           2  2025-01-14 08:42:00+00:00   13.450000
2   3        3           2  2025-01-15 09:47:00+00:00  105.616667
3   4        3           2  2025-01-15 09:47:00+00:00   40.650000
4   5        4           3  2025-01-15 11:49:00+00:00   39.566667

In [118]:
assert not shipment_times_df.isna().any().any()

In [119]:
if "id" in shipment_times_df.columns:
    shipment_times_df.drop(columns=["id"], inplace=True)

data = shipment_times_df.to_dict('records')
assert len(data) == len(shipment_times_df)

data

[{'site_id': 1,
  'carrier_id': 2,
  'created_at': '2025-01-13 09:19:00+00:00',
  'hours': 102.13333333333334},
 {'site_id': 1,
  'carrier_id': 2,
  'created_at': '2025-01-14 08:42:00+00:00',
  'hours': 13.45},
 {'site_id': 3,
  'carrier_id': 2,
  'created_at': '2025-01-15 09:47:00+00:00',
  'hours': 105.61666666666666},
 {'site_id': 3,
  'carrier_id': 2,
  'created_at': '2025-01-15 09:47:00+00:00',
  'hours': 40.65},
 {'site_id': 4,
  'carrier_id': 3,
  'created_at': '2025-01-15 11:49:00+00:00',
  'hours': 39.56666666666667},
 {'site_id': 8,
  'carrier_id': 1,
  'created_at': '2025-01-17 10:40:00+00:00',
  'hours': 73.4},
 {'site_id': 3,
  'carrier_id': 2,
  'created_at': '2025-01-20 09:23:00+00:00',
  'hours': 91.65},
 {'site_id': 1,
  'carrier_id': 2,
  'created_at': '2025-01-23 08:59:00+00:00',
  'hours': 38.21666666666667},
 {'site_id': 3,
  'carrier_id': 2,
  'created_at': '2025-01-23 09:59:00+00:00',
  'hours': 42.266666666666666},
 {'site_id': 4,
  'carrier_id': 3,
  'created_a

In [120]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 88 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 1,
   'carrier_id': 2,
   'hours': '102.133333'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 1,
   'carrier_id': 2,
   'hours': '13.450000'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 3,
   'carrier_id': 2,
   'hours': '105.616667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 3,
   'carrier_id': 2,
   'hours': '40.650000'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 4,
   'carrier_id': 3,
   'hours': '39.566667'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.03

In [121]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 88 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 1,
   'carrier_id': 2,
   'hours': '102.133333'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 1,
   'carrier_id': 2,
   'hours': '13.450000'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 3,
   'carrier_id': 2,
   'hours': '105.616667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 3,
   'carrier_id': 2,
   'hours': '40.650000'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'site_id': 4,
   'carrier_id': 3,
   'hours': '39.566667'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:36.039Z',
   'updated_at': '2025-07-29T07:13:36.039Z',
   'sit

In [122]:
data = response['data']
assert len(data) == len(shipment_times_df)

### Shipment_time_samples

In [123]:
endpoint = "db/tables/shipment_time_samples"

In [124]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('shipment_time_samples_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'carrier_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'median', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'mean', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'std_dev', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'n', 'type': 'integer', 'nullable': False, 'default': None}]

In [125]:
shipment_time_samples_df = pd.read_csv(CSV_PATH + "shipment_time_sample.csv")
shipment_time_samples_df.head()

id  site_id  carrier_id              created_at     median       mean  \
0   1        1           2  2025-07-26T09:48+00:00  26.300000  42.045833   
1   2        2           2  2025-07-26T09:48+00:00  29.900000  35.616667   
2   3        4           3  2025-07-26T09:48+00:00  38.866667  51.212500   
3   4        5           3  2025-07-26T09:48+00:00  18.300000  18.300000   
4   5        6           3  2025-07-26T09:48+00:00  62.333333  70.355556   

     std_dev  n  
0  36.083603  4  
1  10.794349  3  
2  23.855111  4  
3   0.000000  1  
4  31.741976  3

In [126]:
assert not shipment_time_samples_df.isna().any().any()

In [127]:
if "id" in shipment_time_samples_df.columns:
    shipment_time_samples_df.drop(columns=["id"], inplace=True)

data = shipment_time_samples_df.to_dict('records')
assert len(data) == len(shipment_time_samples_df)

data

[{'site_id': 1,
  'carrier_id': 2,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 26.3,
  'mean': 42.04583333333333,
  'std_dev': 36.08360349206025,
  'n': 4},
 {'site_id': 2,
  'carrier_id': 2,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 29.9,
  'mean': 35.61666666666667,
  'std_dev': 10.79434865857885,
  'n': 3},
 {'site_id': 4,
  'carrier_id': 3,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 38.86666666666667,
  'mean': 51.212500000000006,
  'std_dev': 23.85511060723327,
  'n': 4},
 {'site_id': 5,
  'carrier_id': 3,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 18.3,
  'mean': 18.3,
  'std_dev': 0.0,
  'n': 1},
 {'site_id': 6,
  'carrier_id': 3,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 62.333333333333336,
  'mean': 70.35555555555555,
  'std_dev': 31.74197575280023,
  'n': 3},
 {'site_id': 7,
  'carrier_id': 4,
  'created_at': '2025-07-26T09:48+00:00',
  'median': 43.9,
  'mean': 43.9,
  'std_dev': 0.0,
  'n': 1},
 {'site_id': 8,
  'carri

In [128]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 21 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 1,
   'carrier_id': 2,
   'median': '26.300000',
   'mean': '42.045833',
   'std_dev': '36.083603',
   'n': 4},
  {'id': 2,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 2,
   'carrier_id': 2,
   'median': '29.900000',
   'mean': '35.616667',
   'std_dev': '10.794349',
   'n': 3},
  {'id': 3,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 4,
   'carrier_id': 3,
   'median': '38.866667',
   'mean': '51.212500',
   'std_dev': '23.855111',
   'n': 4},
  {'id': 4,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 5,
   'carrier_id': 3,
   'median': '18.300000',
   'mean': '18.300000',
   'std_dev': '0.000000',
   'n': 1},
  {'id': 5,
 

In [129]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 21 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 1,
   'carrier_id': 2,
   'median': '26.300000',
   'mean': '42.045833',
   'std_dev': '36.083603',
   'n': 4},
  {'id': 2,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 2,
   'carrier_id': 2,
   'median': '29.900000',
   'mean': '35.616667',
   'std_dev': '10.794349',
   'n': 3},
  {'id': 3,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 4,
   'carrier_id': 3,
   'median': '38.866667',
   'mean': '51.212500',
   'std_dev': '23.855111',
   'n': 4},
  {'id': 4,
   'created_at': '2025-07-29T07:13:38.079Z',
   'updated_at': '2025-07-29T07:13:38.079Z',
   'site_id': 5,
   'carrier_id': 3,
   'median': '18.300000',
   'mean': '18.300000',
   'std_dev': '0.000000',
   'n': 1},
  {'id': 5,
   'created_a

In [130]:
data = response['data']
assert len(data) == len(shipment_time_samples_df)

### Shipment_time_gammas

In [131]:
endpoint = "db/tables/shipment_time_gammas"

In [132]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('shipment_time_gammas_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'carrier_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'shape', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'loc', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'scale', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'skewness', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'kurtosis', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'mean', 'type': 'numeric', 'nullable': False, 'default': None},
 {'name': 'std_dev', 'type': '

In [133]:
shipment_time_gammas_df = pd.read_csv(CSV_PATH + "shipment_time_gamma.csv")
shipment_time_gammas_df.head()

id  site_id  carrier_id     shape        loc      scale  skewness  \
0   1        3           2  1.211887  31.021468  21.282943   0.87955   

   kurtosis  median    mean    std_dev   n  
0 -0.457561  45.875  56.814  22.171215  50

In [134]:
assert not shipment_time_gammas_df.isna().any().any()

In [135]:
if "id" in shipment_time_gammas_df.columns:
    shipment_time_gammas_df.drop(columns=["id"], inplace=True)

if "median" in shipment_time_gammas_df.columns:
    shipment_time_gammas_df.drop(columns=["median"], inplace=True)

data = shipment_time_gammas_df.to_dict('records')
assert len(data) == len(shipment_time_gammas_df)

data

[{'site_id': 3,
  'carrier_id': 2,
  'shape': 1.211886691269898,
  'loc': 31.021468212563512,
  'scale': 21.282943184186703,
  'skewness': 0.8795501880949239,
  'kurtosis': -0.4575613325204886,
  'mean': 56.81400000000001,
  'std_dev': 22.171215164248675,
  'n': 50}]

In [136]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:39.483Z',
   'updated_at': '2025-07-29T07:13:39.483Z',
   'site_id': 3,
   'carrier_id': 2,
   'shape': '1.211887',
   'loc': '31.021468',
   'scale': '21.282943',
   'skewness': '0.879550',
   'kurtosis': '-0.457561',
   'mean': '56.814000',
   'std_dev': '22.171215',
   'n': 50}],
 'meta': {'recordsAffected': 1, 'executionTime': 344},
 'timestamp': '2025-07-29T07:13:39.499Z'}

In [137]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 1 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:39.483Z',
   'updated_at': '2025-07-29T07:13:39.483Z',
   'site_id': 3,
   'carrier_id': 2,
   'shape': '1.211887',
   'loc': '31.021468',
   'scale': '21.282943',
   'skewness': '0.879550',
   'kurtosis': '-0.457561',
   'mean': '56.814000',
   'std_dev': '22.171215',
   'n': 50}],
 'meta': {'recordsAffected': 1, 'executionTime': 216},
 'timestamp': '2025-07-29T07:13:39.842Z'}

In [138]:
data = response['data']
assert len(data) == len(shipment_time_gammas_df)

### Holidays

In [139]:
endpoint = "db/tables/holidays"

In [140]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('holidays_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'country_code',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'category', 'type': 'text', 'nullable': False, 'default': None},
 {'name': 'description', 'type': 'text', 'nullable': True, 'default': None},
 {'name': 'url', 'type': 'text', 'nullable': True, 'default': None},
 {'name': 'type',
  'type': 'character varying',
  'nullable': True,
  'default': None},
 {'name': 'date', 'type': 'date', 'nullable': False, 'default': None},
 {'name': 'week_day', 'type': 'integer', 'nullable': False, 'default': None},
 {'na

In [141]:
holidays_df = pd.read_csv(CSV_PATH + "holiday.csv")
holidays_df.head()

id                 name country_code category  \
0   1  Special Working Day           BY  WORKING   
1   2          Victory Day           BA  WORKING   
2   3  Special Working Day           CN  WORKING   
3   4  Special Working Day           CN  WORKING   
4   5  Special Working Day           CN  WORKING   

                                         description  \
0  Special Working Day is a working day on weeken...   
1  Victory Day is a working holiday in Bosnia-Her...   
2  Special Working Day is a working day on a week...   
3  Special Working Day is a working day on a week...   
4  Special Working Day is a working day on a week...   

                                                 url  \
0  https://calendarific.com/holiday/belarus/speci...   
1  https://calendarific.com/holiday/bosnia/victor...   
2  https://calendarific.com/holiday/china/spring-...   
3  https://calendarific.com/holiday/china/spring-...   
4  https://calendarific.com/holiday/china/labour-...   

                       type        date  week_day  month  year_day  
0    Working day on weekend  2025-01-11         6      1        11  
1           Working holiday  2025-05-09         5      5       129  
2  Working day on a weekend  2025-01-26         7      1        26  
3  Working day on a weekend  2025-02-08         6      2        39  
4  Working day on a weekend  2025-04-27         7      4       117

In [142]:
holidays_df[holidays_df["country_code"].isna()]

id                                               name country_code  \
2195  2196                                           New Year          NaN   
2196  2197                                   Independence Day          NaN   
2197  2198                                        Good Friday          NaN   
2198  2199                                      Easter Monday          NaN   
2199  2200                                       Workers' Day          NaN   
2200  2201                                       Cassinga Day          NaN   
2201  2202                              Cassinga Day observed          NaN   
2202  2203                                         Africa Day          NaN   
2203  2204                                Africa Day observed          NaN   
2204  2205                           Genocide Remembrance Day          NaN   
2205  2206                                      Ascension Day          NaN   
2206  2207                                        Heroes' Day          NaN   
2207  2208  Day of the Namibian Women and International Hu...          NaN   
2208  2209                                      Christmas Day          NaN   
2209  2210                                         Family Day          NaN   

     category                                        description  \
2195  CLOSURE  New Year’s Day is the first day of the year, o...   
2196  CLOSURE    Independence Day is a public holiday in Namibia   
2197  CLOSURE  Good Friday is a global Christian observance t...   
2198  CLOSURE      Easter Monday is the day after Easter Sunday.   
2199  CLOSURE  Labor Day, International Workers' Day, and May...   
2200  CLOSURE        Cassinga Day is a public holiday in Namibia   
2201  CLOSURE        Cassinga Day is a public holiday in Namibia   
2202  CLOSURE          Africa Day is a public holiday in Namibia   
2203  CLOSURE          Africa Day is a public holiday in Namibia   
2204  CLOSURE  Genocide Remembrance Day is a public holiday i...   
2205  CLOSURE  Ascension Day is the 40th day of Easter. It is...   
2206  CLOSURE         Heroes' Day is a public holiday in Namibia   
2207  CLOSURE  Day of the Namibian Women and International Hu...   
2208  CLOSURE  Christmas Day is one of the biggest Christian ...   
2209  CLOSURE          Family Day is a public holiday in Namibia   

                                                    url            type  \
2195  https://calendarific.com/holiday/namibia/new-year  Public holiday   
2196  https://calendarific.com/holiday/namibia/indep...  Public holiday   
2197  https://calendarific.com/holiday/namibia/good-...  Public holiday   
2198  https://calendarific.com/holiday/namibia/easte...  Public holiday   
2199   https://calendarific.com/holiday/namibia/may-day  Public holiday   
2200  https://calendarific.com/holiday/namibia/cassi...  Public holiday   
2201  https://calendarific.com/holiday/namibia/cassi...  Public holiday   
2202  https://calendarific.com/holiday/namibia/afric...  Public holiday   
2203  https://calendarific.com/holiday/namibia/afric...  Public holiday   
2204  https://calendarific.com/holiday/namibia/genoc...  Public holiday   
2205  https://calendarific.com/holiday/namibia/ascen...  Public holiday   
2206  https://calendarific.com/holiday/namibia/heroe...  Public holiday   
2207  https://calendarific.com/holiday/namibia/inter...  Public holiday   
2208  https://calendarific.com/holiday/namibia/chris...  Public holiday   
2209  https://calendarific.com/holiday/namibia/day-o...  Public holiday   

            date  week_day  month  year_day  
2195  2025-01-01         3      1         1  
2196  2025-03-21         5      3        80  
2197  2025-04-18         5      4       108  
2198  2025-04-21         1      4       111  
2199  2025-05-01         4      5       121  
2200  2025-05-04         7      5       124  
2201  2025-05-05         1      5       125  
2202  2025-05-25         7      5       145  
2203  2025-05-26         1      5       146  
2204  202

In [143]:
holidays_df.loc[holidays_df["country_code"].isna(), 'country_code'] = "NA"
assert len(holidays_df[holidays_df["country_code"].isna()]) == 0

In [144]:
for col in [
    "description", 
    "url",
    "type", 
]:
    holidays_df[col] = holidays_df[col].astype("object").where(pd.notnull(holidays_df[col]), None)

In [145]:
if "id" in holidays_df.columns:
    holidays_df.drop(columns=["id"], inplace=True)

data = holidays_df.to_dict('records')
assert len(data) == len(holidays_df)

data

[{'name': 'Special Working Day',
  'country_code': 'BY',
  'category': 'WORKING',
  'description': 'Special Working Day is a working day on weekend in Belarus',
  'url': 'https://calendarific.com/holiday/belarus/special-working-day-january',
  'type': 'Working day on weekend',
  'date': '2025-01-11',
  'week_day': 6,
  'month': 1,
  'year_day': 11},
 {'name': 'Victory Day',
  'country_code': 'BA',
  'category': 'WORKING',
  'description': 'Victory Day is a working holiday in Bosnia-Herzegovina',
  'url': 'https://calendarific.com/holiday/bosnia/victory-day',
  'type': 'Working holiday',
  'date': '2025-05-09',
  'week_day': 5,
  'month': 5,
  'year_day': 129},
 {'name': 'Special Working Day',
  'country_code': 'CN',
  'category': 'WORKING',
  'description': 'Special Working Day is a working day on a weekend in China',
  'url': 'https://calendarific.com/holiday/china/spring-festival-moved-weekend-7',
  'type': 'Working day on a weekend',
  'date': '2025-01-26',
  'week_day': 7,
  'month

In [146]:
response = post_request(endpoint, {"data": data})

In [147]:
'''
import math

chunk_size = 500
sub_chunk_size = 25

total_chunks = math.ceil(len(data) / chunk_size)

for i in range(0, len(data), chunk_size):
    current_chunk = i // chunk_size + 1
    chunk = data[i:i + chunk_size]
    print(f"Processing chunk {current_chunk} of {total_chunks}: chunk size {len(chunk)}")
    
    try:
        response = post_request(endpoint, {"data": chunk})
    except:
        print(f"Failed to process chunk {current_chunk}: passing to sub-chunks")
        for j in range(0, len(chunk), sub_chunk_size):
            sub_chunk = chunk[j:j + sub_chunk_size]
            print(f"Processing sub-chunk {j // sub_chunk_size + 1} of {math.ceil(len(chunk) / sub_chunk_size)}: sub-chunk size {len(sub_chunk)}")
        
            try:
                response = post_request(endpoint, {"data": sub_chunk})
            except Exception as e:
                print(f"Failed to process sub-chunk {j // sub_chunk_size + 1}: passing to single entries")
                for record in sub_chunk:
                    try:
                        response = post_request(endpoint, {"data": [record]})
                    except Exception as e:
                        print(f"Failed to process record: {record}. Passing to next record.")       
'''                      

'\nimport math\n\nchunk_size = 500\nsub_chunk_size = 25\n\ntotal_chunks = math.ceil(len(data) / chunk_size)\n\nfor i in range(0, len(data), chunk_size):\n    current_chunk = i // chunk_size + 1\n    chunk = data[i:i + chunk_size]\n    print(f"Processing chunk {current_chunk} of {total_chunks}: chunk size {len(chunk)}")\n\n    try:\n        response = post_request(endpoint, {"data": chunk})\n    except:\n        print(f"Failed to process chunk {current_chunk}: passing to sub-chunks")\n        for j in range(0, len(chunk), sub_chunk_size):\n            sub_chunk = chunk[j:j + sub_chunk_size]\n            print(f"Processing sub-chunk {j // sub_chunk_size + 1} of {math.ceil(len(chunk) / sub_chunk_size)}: sub-chunk size {len(sub_chunk)}")\n\n            try:\n                response = post_request(endpoint, {"data": sub_chunk})\n            except Exception as e:\n                print(f"Failed to process sub-chunk {j // sub_chunk_size + 1}: passing to single entries")\n                for

In [148]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 3609 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:43.279Z',
   'updated_at': '2025-07-29T07:13:43.279Z',
   'name': 'Special Working Day',
   'country_code': 'BY',
   'category': 'WORKING',
   'description': 'Special Working Day is a working day on weekend in Belarus',
   'url': 'https://calendarific.com/holiday/belarus/special-working-day-january',
   'type': 'Working day on weekend',
   'date': '2025-01-11T00:00:00.000Z',
   'week_day': 6,
   'month': 1,
   'year_day': 11},
  {'id': 2,
   'created_at': '2025-07-29T07:13:43.279Z',
   'updated_at': '2025-07-29T07:13:43.279Z',
   'name': 'Victory Day',
   'country_code': 'BA',
   'category': 'WORKING',
   'description': 'Victory Day is a working holiday in Bosnia-Herzegovina',
   'url': 'https://calendarific.com/holiday/bosnia/victory-day',
   'type': 'Working holiday',
   'date': '2025-05-09T00:00:00.000Z',
   'week_day': 5,
   'month': 5,
   'year_day': 129},
  {'id': 3,
 

In [149]:
data = response['data']
assert len(data) == len(holidays_df)

### OTI

In [150]:
endpoint = "db/tables/overall_transit_indices"

In [151]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('overall_transit_indices_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'source_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'destination_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'hours', 'type': 'numeric', 'nullable': False, 'default': None}]

In [152]:
oti_df = pd.read_csv(CSV_PATH + "oti.csv")
oti_df.head()

id  source_id  destination_id                 created_at      hours
0   1          5              63  2025-07-26T10:05:07+00:00   8.400000
1   2         63              39  2025-07-26T10:05:07+00:00   3.683333
2   3         39              20  2025-07-26T10:05:07+00:00  18.966667
3   4         20              19  2025-07-26T10:05:07+00:00   1.983333
4   5         19              40  2025-07-26T10:05:07+00:00   1.450000

In [153]:
assert not oti_df.isna().any().any()

In [154]:
if "id" in oti_df.columns:
    oti_df.drop(columns=["id"], inplace=True)

data = oti_df.to_dict('records')
assert len(data) == len(oti_df)

data

[{'source_id': 5,
  'destination_id': 63,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 8.4},
 {'source_id': 63,
  'destination_id': 39,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 3.683333333333333},
 {'source_id': 39,
  'destination_id': 20,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 18.966666666666665},
 {'source_id': 20,
  'destination_id': 19,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 1.9833333333333327},
 {'source_id': 19,
  'destination_id': 40,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 1.45},
 {'source_id': 40,
  'destination_id': 58,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 0.7333333333333333},
 {'source_id': 58,
  'destination_id': 34,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 2.2},
 {'source_id': 31,
  'destination_id': 47,
  'created_at': '2025-07-26T10:05:07+00:00',
  'hours': 10.466666666666669},
 {'source_id': 47,
  'destination_id': 65,
  'created_at': '2025-07-26T10:05:07+00:00'

In [155]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 562 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 5,
   'destination_id': 63,
   'hours': '8.400000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 63,
   'destination_id': 39,
   'hours': '3.683333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 39,
   'destination_id': 20,
   'hours': '18.966667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 20,
   'destination_id': 19,
   'hours': '1.983333'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 19,
   'destination_id': 40,
   'hours': '1.450000'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:51.184Z',
   'up

In [156]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 562 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 5,
   'destination_id': 63,
   'hours': '8.400000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 63,
   'destination_id': 39,
   'hours': '3.683333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 39,
   'destination_id': 20,
   'hours': '18.966667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 20,
   'destination_id': 19,
   'hours': '1.983333'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '2025-07-29T07:13:51.184Z',
   'source_id': 19,
   'destination_id': 40,
   'hours': '1.450000'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:51.184Z',
   'updated_at': '

In [157]:
data = response['data']
assert len(data) == len(oti_df)

### ORI

In [158]:
endpoint = "db/tables/overall_residence_indices"

In [159]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('overall_residence_indices_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'vertex_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'hours', 'type': 'numeric', 'nullable': False, 'default': None}]

In [160]:
ori_df = pd.read_csv(CSV_PATH + "ori.csv")
ori_df.head()

id  vertex_id                 created_at      hours
0   1         63  2025-07-26T10:05:00+00:00   0.416667
1   2         39  2025-07-26T10:05:00+00:00  30.283333
2   3         20  2025-07-26T10:05:00+00:00   0.016667
3   4         19  2025-07-26T10:05:00+00:00   3.016667
4   5         40  2025-07-26T10:05:00+00:00   1.766667

In [161]:
assert not ori_df.isna().any().any()

In [162]:
if "id" in ori_df.columns:
    ori_df.drop(columns=["id"], inplace=True)

data = ori_df.to_dict('records')
assert len(data) == len(ori_df)

data

[{'vertex_id': 63,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 0.4166666666666667},
 {'vertex_id': 39,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 30.28333333333333},
 {'vertex_id': 20,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 0.0166666666666666},
 {'vertex_id': 19,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 3.0166666666666666},
 {'vertex_id': 40,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 1.7666666666666666},
 {'vertex_id': 58,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 0.4833333333333333},
 {'vertex_id': 65,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 1.3166666666666669},
 {'vertex_id': 7, 'created_at': '2025-07-26T10:05:00+00:00', 'hours': 4.35},
 {'vertex_id': 23,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 1.4833333333333334},
 {'vertex_id': 60, 'created_at': '2025-07-26T10:05:00+00:00', 'hours': 70.85},
 {'vertex_id': 56,
  'created_at': '2025-07-26T10:05:00+00:00',
  'hours': 73

In [163]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 371 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 63,
   'hours': '0.416667'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 39,
   'hours': '30.283333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 20,
   'hours': '0.016667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 19,
   'hours': '3.016667'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 40,
   'hours': '1.766667'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 58,
   'hours': '0.483333'},
  {'id': 7,
   'created_at': '2025-07-29

In [164]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 371 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 63,
   'hours': '0.416667'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 39,
   'hours': '30.283333'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 20,
   'hours': '0.016667'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 19,
   'hours': '3.016667'},
  {'id': 5,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 40,
   'hours': '1.766667'},
  {'id': 6,
   'created_at': '2025-07-29T07:13:53.342Z',
   'updated_at': '2025-07-29T07:13:53.342Z',
   'vertex_id': 58,
   'hours': '0.483333'},
  {'id': 7,
   'created_at': '2025-07-29T07:13:53.34

In [165]:
data = response['data']
assert len(data) == len(ori_df)

### WMI

In [166]:
endpoint = "db/tables/weather_meta_indices"

In [167]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('weather_meta_indices_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'estimated_time_id',
  'type': 'integer',
  'nullable': True,
  'default': None},
 {'name': 'source_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'destination_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'timestamp',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': None},
 {'name': 'n_interpolation_points',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'step_distance_km',
  'type': 'numeric',
  'nullable': False,
  'default': None},
 {'name': 'value', 'type': 'numeric', 'nullable': False, 'default': None}]

In [168]:
wmi_df = pd.read_csv(CSV_PATH + "wmi.csv")
wmi_df.head()

id  source_id  destination_id               timestamp  \
0   0         63              39  2025-01-14T21:46+00:00   
1   1         39              20  2025-01-16T18:16+00:00   
2   2         20              19  2025-01-16T23:44+00:00   
3   3         19              40  2025-01-17T05:20+00:00   
4   4         40              58  2025-01-17T07:15+00:00   

                  created_at  n_interpolation_points  step_distance_km  \
0  2025-07-26T10:05:10+00:00                       2         200.00000   
1  2025-07-26T10:05:10+00:00                       5        2345.47108   
2  2025-07-26T10:05:10+00:00                       4         200.00000   
3  2025-07-26T10:05:10+00:00                       5         200.00000   
4  2025-07-26T10:05:10+00:00                       2         200.00000   

      value  
0  0.224436  
1  0.750000  
2  0.101561  
3  0.119203  
4  0.103400

In [169]:
assert not wmi_df.isna().any().any()

In [170]:
if "id" in wmi_df.columns:
    wmi_df.drop(columns=["id"], inplace=True)

data = wmi_df.to_dict('records')
assert len(data) == len(wmi_df)

data

[{'source_id': 63,
  'destination_id': 39,
  'timestamp': '2025-01-14T21:46+00:00',
  'created_at': '2025-07-26T10:05:10+00:00',
  'n_interpolation_points': 2,
  'step_distance_km': 200.0,
  'value': 0.2244359857309265},
 {'source_id': 39,
  'destination_id': 20,
  'timestamp': '2025-01-16T18:16+00:00',
  'created_at': '2025-07-26T10:05:10+00:00',
  'n_interpolation_points': 5,
  'step_distance_km': 2345.471079985375,
  'value': 0.75},
 {'source_id': 20,
  'destination_id': 19,
  'timestamp': '2025-01-16T23:44+00:00',
  'created_at': '2025-07-26T10:05:10+00:00',
  'n_interpolation_points': 4,
  'step_distance_km': 200.0,
  'value': 0.1015609278976366},
 {'source_id': 19,
  'destination_id': 40,
  'timestamp': '2025-01-17T05:20+00:00',
  'created_at': '2025-07-26T10:05:10+00:00',
  'n_interpolation_points': 5,
  'step_distance_km': 200.0,
  'value': 0.1192029220221175},
 {'source_id': 40,
  'destination_id': 58,
  'timestamp': '2025-01-17T07:15+00:00',
  'created_at': '2025-07-26T10:05:

In [171]:
data[0]

{'source_id': 63,
 'destination_id': 39,
 'timestamp': '2025-01-14T21:46+00:00',
 'created_at': '2025-07-26T10:05:10+00:00',
 'n_interpolation_points': 2,
 'step_distance_km': 200.0,
 'value': 0.2244359857309265}

In [172]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 483 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 63,
   'destination_id': 39,
   'timestamp': '2025-01-14T21:46:00.000Z',
   'n_interpolation_points': 2,
   'step_distance_km': '200.00',
   'value': '0.2244360'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 39,
   'destination_id': 20,
   'timestamp': '2025-01-16T18:16:00.000Z',
   'n_interpolation_points': 5,
   'step_distance_km': '2345.47',
   'value': '0.7500000'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 20,
   'destination_id': 19,
   'timestamp': '2025-01-16T23:44:00.000Z',
   'n_interpolation_points': 4,
   'step_distance_km': '200.00',
   'value': 

In [173]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 483 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 63,
   'destination_id': 39,
   'timestamp': '2025-01-14T21:46:00.000Z',
   'n_interpolation_points': 2,
   'step_distance_km': '200.00',
   'value': '0.2244360'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 39,
   'destination_id': 20,
   'timestamp': '2025-01-16T18:16:00.000Z',
   'n_interpolation_points': 5,
   'step_distance_km': '2345.47',
   'value': '0.7500000'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:56.106Z',
   'updated_at': '2025-07-29T07:13:56.106Z',
   'estimated_time_id': None,
   'source_id': 20,
   'destination_id': 19,
   'timestamp': '2025-01-16T23:44:00.000Z',
   'n_interpolation_points': 4,
   'step_distance_km': '200.00',
   'value': '0.1015609'}

In [174]:
data = response['data']
assert len(data) == len(wmi_df)

### TMI

In [175]:
endpoint = "db/tables/traffic_meta_indices"

In [176]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('traffic_meta_indices_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'estimated_time_id',
  'type': 'integer',
  'nullable': True,
  'default': None},
 {'name': 'source_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'destination_id',
  'type': 'integer',
  'nullable': False,
  'default': None},
 {'name': 'timestamp',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': None},
 {'name': 'transportation_mode',
  'type': 'text',
  'nullable': False,
  'default': None},
 {'name': 'value', 'type': 'numeric', 'nullable': False, 'default': None}]

In [177]:
tmi_df = pd.read_csv(CSV_PATH + "tmi.csv")
tmi_df.head()

id  source_id  destination_id                  timestamp  \
0   1         63              39  2025-01-14 18:05:00+00:00   
1   2         40              58  2025-01-17 07:15:00+00:00   
2   3         58              31  2025-01-17 08:28:00+00:00   
3   4         47              65  2025-01-09 18:30:00+00:00   
4   5         23              60  2025-01-10 05:55:00+00:00   

                  created_at transportation_mode     value  
0  2025-07-26T10:05:14+00:00                ROAD  0.000000  
1  2025-07-26T10:05:14+00:00                ROAD  0.148110  
2  2025-07-26T10:05:14+00:00                ROAD  0.231534  
3  2025-07-26T10:05:14+00:00                ROAD  0.056662  
4  2025-07-26T10:05:14+00:00                ROAD  0.097354

In [178]:
assert not tmi_df.isna().any().any()

In [179]:
if "id" in tmi_df.columns:
    tmi_df.drop(columns=["id"], inplace=True)

data = tmi_df.to_dict('records')
assert len(data) == len(tmi_df)

data

[{'source_id': 63,
  'destination_id': 39,
  'timestamp': '2025-01-14 18:05:00+00:00',
  'created_at': '2025-07-26T10:05:14+00:00',
  'transportation_mode': 'ROAD',
  'value': 0.0},
 {'source_id': 40,
  'destination_id': 58,
  'timestamp': '2025-01-17 07:15:00+00:00',
  'created_at': '2025-07-26T10:05:14+00:00',
  'transportation_mode': 'ROAD',
  'value': 0.1481103166496425},
 {'source_id': 58,
  'destination_id': 31,
  'timestamp': '2025-01-17 08:28:00+00:00',
  'created_at': '2025-07-26T10:05:14+00:00',
  'transportation_mode': 'ROAD',
  'value': 0.231534090909091},
 {'source_id': 47,
  'destination_id': 65,
  'timestamp': '2025-01-09 18:30:00+00:00',
  'created_at': '2025-07-26T10:05:14+00:00',
  'transportation_mode': 'ROAD',
  'value': 0.0566624017547065},
 {'source_id': 23,
  'destination_id': 60,
  'timestamp': '2025-01-10 05:55:00+00:00',
  'created_at': '2025-07-26T10:05:14+00:00',
  'transportation_mode': 'ROAD',
  'value': 0.0973544973544971},
 {'source_id': 60,
  'destinati

In [180]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 218 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 63,
   'destination_id': 39,
   'timestamp': '2025-01-14T18:05:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.0000000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 40,
   'destination_id': 58,
   'timestamp': '2025-01-17T07:15:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.1481103'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 58,
   'destination_id': 31,
   'timestamp': '2025-01-17T08:28:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.2315341'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-

In [181]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 218 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 63,
   'destination_id': 39,
   'timestamp': '2025-01-14T18:05:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.0000000'},
  {'id': 2,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 40,
   'destination_id': 58,
   'timestamp': '2025-01-17T07:15:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.1481103'},
  {'id': 3,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:58.544Z',
   'estimated_time_id': None,
   'source_id': 58,
   'destination_id': 31,
   'timestamp': '2025-01-17T08:28:00.000Z',
   'transportation_mode': 'ROAD',
   'value': '0.2315341'},
  {'id': 4,
   'created_at': '2025-07-29T07:13:58.544Z',
   'updated_at': '2025-07-29T07:13:

In [182]:
data = response['data']
assert len(data) == len(tmi_df)

### SCGraph update

In [183]:
response: requests.Response = requests.post(f"{BASE_URL}lcdi/sc-graph")
response.raise_for_status()
assert response.status_code == 201

### Params

In [184]:
endpoint = "db/tables/params"

In [185]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('params_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'name',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'general_category',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'category',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'description', 'type': 'text', 'nullable': True, 'default': None},
 {'name': 'value', 'type': 'numeric', 'nullable': False, 'default': None}]

In [186]:
params_df = pd.read_csv(CSV_PATH + "params.csv")
params_df

id                            name              category general_category  \
0    1  HISTORICAL_DISPATCH_CONFIDENCE         DISPATCH_TIME       HISTORICAL   
1    2  HISTORICAL_SHIPMENT_CONFIDENCE         SHIPMENT_TIME       HISTORICAL   
2    3                   DT_CONFIDENCE         DISPATCH_TIME         REALTIME   
3    4       DISPATCH_CLOSURE_HOLIDAYS               HOLIDAY         REALTIME   
4    5       DISPATCH_WORKING_HOLIDAYS               HOLIDAY         REALTIME   
5    6       DISPATCH_CLOSURE_WEEKENDS               HOLIDAY         REALTIME   
6    7          TMI_AIR_MIN_SPEED_KM_H                   TMI         REALTIME   
7    8          TMI_AIR_MAX_SPEED_KM_H                   TMI         REALTIME   
8    9          TMI_SEA_MIN_SPEED_KM_H                   TMI         REALTIME   
9   10          TMI_SEA_MAX_SPEED_KM_H                   TMI         REALTIME   
10  11         TMI_RAIL_MIN_SPEED_KM_H                   TMI         REALTIME   
11  12         TMI_RAIL_MAX_SPEED_KM_H                   TMI         REALTIME   
12  13         TMI_ROAD_MIN_SPEED_KM_H                   TMI         REALTIME   
13  14         TMI_ROAD_MAX_SPEED_KM_H                   TMI         REALTIME   
14  15         TMI_AIR_MIN_DISTANCE_KM                   TMI         REALTIME   
15  16         TMI_AIR_MAX_DISTANCE_KM                   TMI         REALTIME   
16  17         TMI_SEA_MIN_DISTANCE_KM                   TMI         REALTIME   
17  18         TMI_SEA_MAX_DISTANCE_KM                   TMI         REALTIME   
18  19        TMI_RAIL_MIN_DISTANCE_KM                   TMI         REALTIME   
19  20        TMI_RAIL_MAX_DISTANCE_KM                   TMI         REALTIME   
20  21        TMI_ROAD_MIN_DISTANCE_KM                   TMI         REALTIME   
21  22        TMI_ROAD_MAX_DISTANCE_KM                   TMI         REALTIME   
22  23         TMI_USE_TRAFFIC_SERVICE                   TMI         REALTIME   
23  24        TMI_TRAFFIC_MAX_TIMEDIFF                   TMI         REALTIME   
24  25         WMI_USE_WEATHER_SERVICE                   WMI         REALTIME   
25  26        WMI_WEATHER_MAX_TIMEDIFF                   WMI         REALTIME   
26  27            WMI_STEP_DISTANCE_KM                   WMI         REALTIME   
27  28                  WMI_MAX_POINTS                   WMI         REALTIME   
28  29         RT_ESTIMATOR_MODEL_MAPE  ROUTE_TIME_ESTIMATOR         REALTIME   
29  30          USE_RT_ESTIMATOR_MODEL  ROUTE_TIME_ESTIMATOR         REALTIME   
30  31               ALPHA_CONST_VALUE                 ALPHA         REALTIME   
31  32           ALPHA_CALCULATOR_TYPE                 ALPHA         REALTIME   
32  33         PT_PATH_MIN_PROBABILITY                    PT         REALTIME   
33  34                    PT_MAX_PATHS                    PT         REALTIME   
34  35     PT_EXT_DATA_MIN_PROBABILITY                    PT         REALTIME   
35  36                   PT_CONFIDENCE                    PT         REALTIME   
36  37                   TT_CONFIDENCE                    TT         REALTIME   
37  38                  TFST_TOLERANCE                  TFST         REALTIME   
38  39       DELAY_DISPATCH_CONFIDENCE         DISPATCH_TIME         REALTIME   
39  40       DELAY_SHIPMENT_CONFIDENCE         SHIPMENT_TIME         REALTIME   
40  41                 PARALLELIZATION                SYSTEM           SYSTEM   

                                          description         value  
0           Historical dispatch time confidence level  9.000000e-01  
1           Historical shipment time confidence level  9.000000e-01  
2                            Dispatch time confidence  9.000000e-01  
3   Whether to consider closure holidays in the di...  1.000000e+00  
4   Whether to consider working holidays in the di...  1.000000e+00  
5   Whether to consider weekends as holidays in th...  1.000000e+00  
6    Minimum air speed used in TMI calculation (km/h)  2.000000e+02  
7    Maximum air speed used in TMI calcul

In [187]:
assert not params_df.isna().any().any()

In [188]:
if "id" in params_df.columns:
    params_df.drop(columns=["id"], inplace=True)

data = params_df.to_dict('records')
assert len(data) == len(params_df)

data

[{'name': 'HISTORICAL_DISPATCH_CONFIDENCE',
  'category': 'DISPATCH_TIME',
  'general_category': 'HISTORICAL',
  'description': 'Historical dispatch time confidence level',
  'value': 0.9},
 {'name': 'HISTORICAL_SHIPMENT_CONFIDENCE',
  'category': 'SHIPMENT_TIME',
  'general_category': 'HISTORICAL',
  'description': 'Historical shipment time confidence level',
  'value': 0.9},
 {'name': 'DT_CONFIDENCE',
  'category': 'DISPATCH_TIME',
  'general_category': 'REALTIME',
  'description': 'Dispatch time confidence',
  'value': 0.9},
 {'name': 'DISPATCH_CLOSURE_HOLIDAYS',
  'category': 'HOLIDAY',
  'general_category': 'REALTIME',
  'description': 'Whether to consider closure holidays in the dispatch time estimation',
  'value': 1.0},
 {'name': 'DISPATCH_WORKING_HOLIDAYS',
  'category': 'HOLIDAY',
  'general_category': 'REALTIME',
  'description': 'Whether to consider working holidays in the dispatch time estimation',
  'value': 1.0},
 {'name': 'DISPATCH_CLOSURE_WEEKENDS',
  'category': 'HOLI

In [189]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 41 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'HISTORICAL_DISPATCH_CONFIDENCE',
   'general_category': 'HISTORICAL',
   'category': 'DISPATCH_TIME',
   'description': 'Historical dispatch time confidence level',
   'value': '0.900000'},
  {'id': 2,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'HISTORICAL_SHIPMENT_CONFIDENCE',
   'general_category': 'HISTORICAL',
   'category': 'SHIPMENT_TIME',
   'description': 'Historical shipment time confidence level',
   'value': '0.900000'},
  {'id': 3,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'DT_CONFIDENCE',
   'general_category': 'REALTIME',
   'category': 'DISPATCH_TIME',
   'description': 'Dispatch time confidence',
   'value': '0.900000'},
  {'id': 4,
   'created_at': '2025-07-29T07:14:0

In [190]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 41 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'HISTORICAL_DISPATCH_CONFIDENCE',
   'general_category': 'HISTORICAL',
   'category': 'DISPATCH_TIME',
   'description': 'Historical dispatch time confidence level',
   'value': '0.900000'},
  {'id': 2,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'HISTORICAL_SHIPMENT_CONFIDENCE',
   'general_category': 'HISTORICAL',
   'category': 'SHIPMENT_TIME',
   'description': 'Historical shipment time confidence level',
   'value': '0.900000'},
  {'id': 3,
   'created_at': '2025-07-29T07:14:05.260Z',
   'updated_at': '2025-07-29T07:14:05.260Z',
   'name': 'DT_CONFIDENCE',
   'general_category': 'REALTIME',
   'category': 'DISPATCH_TIME',
   'description': 'Dispatch time confidence',
   'value': '0.900000'},
  {'id': 4,
   'created_at': '2025-07-29T07:14:05.260Z',
   

In [191]:
data = response['data']
assert len(data) == len(params_df)

### Alphas_opt

In [192]:
endpoint = "db/tables/alphas_opt"

In [193]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('alphas_opt_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'site_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'carrier_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'tt_weight', 'type': 'numeric', 'nullable': False, 'default': '0.5'}]

In [194]:
alphas_opt_df = pd.read_csv(CSV_PATH + "alphas_opt.csv")
alphas_opt_df.head()

id  site_id  carrier_id  tt_weight
0   1        1           1        0.5
1   2        1           2        0.5
2   3        1           3        0.5
3   4        1           4        0.5
4   5        1           5        0.5

In [195]:
assert not alphas_opt_df.isna().any().any()
assert len(alphas_opt_df) == len(carriers_df) * len(sites_df)

In [196]:
if "id" in alphas_opt_df.columns:
    alphas_opt_df.drop(columns=["id"], inplace=True)

data = alphas_opt_df.to_dict('records')
assert len(data) == len(alphas_opt_df)

data

[{'site_id': 1, 'carrier_id': 1, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 2, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 3, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 4, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 5, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 6, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 7, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 8, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 9, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 10, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 11, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 12, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 13, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 14, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 15, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 16, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 17, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 18, 'tt_weight': 0.5},
 {'site_id': 1, 'carrier_id': 19, 'tt_weight': 0.5},
 {

In [197]:
response = post_request(endpoint, {"data": data})
response

{'success': True,
 'message': 'Successfully inserted 420 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 1,
   'tt_weight': '0.500000'},
  {'id': 2,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 2,
   'tt_weight': '0.500000'},
  {'id': 3,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 3,
   'tt_weight': '0.500000'},
  {'id': 4,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 4,
   'tt_weight': '0.500000'},
  {'id': 5,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 5,
   'tt_weight': '0.500000'},
  {'id': 6,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-

In [198]:
response = send_request(endpoint + "/data")
response

{'success': True,
 'message': 'Retrieved 420 record(s)',
 'data': [{'id': 1,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 1,
   'tt_weight': '0.500000'},
  {'id': 2,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 2,
   'tt_weight': '0.500000'},
  {'id': 3,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 3,
   'tt_weight': '0.500000'},
  {'id': 4,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 4,
   'tt_weight': '0.500000'},
  {'id': 5,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.100Z',
   'site_id': 1,
   'carrier_id': 5,
   'tt_weight': '0.500000'},
  {'id': 6,
   'created_at': '2025-07-29T07:14:07.100Z',
   'updated_at': '2025-07-29T07:14:07.

In [199]:
data = response['data']
assert len(data) == len(alphas_opt_df)

### Estimated times

In [200]:
endpoint = "db/tables/estimated_times"

In [201]:
table = send_request(endpoint)
columns = table['data']["columns"]
columns

[{'name': 'id',
  'type': 'integer',
  'nullable': False,
  'default': "nextval('estimated_times_id_seq'::regclass)"},
 {'name': 'created_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'updated_at',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': 'CURRENT_TIMESTAMP'},
 {'name': 'vertex_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'order_id', 'type': 'integer', 'nullable': False, 'default': None},
 {'name': 'shipment_time',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': None},
 {'name': 'event_time',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': None},
 {'name': 'estimation_time',
  'type': 'timestamp with time zone',
  'nullable': False,
  'default': None},
 {'name': 'status',
  'type': 'character varying',
  'nullable': False,
  'default': None},
 {'name': 'DT_weekend_days',
  'type': 'integer',
  'nullable': False,
  'defau

In [202]:
BASE_URL + endpoint + "/all-records"

'https://xug11cb2b1.execute-api.eu-central-1.amazonaws.com/dev/db/tables/estimated_times/all-records'

In [203]:
EMPTY = False
if EMPTY:
    response = requests.delete(BASE_URL + endpoint + "/all-records", json={"confirmDeleteAll": True, "tableNameConfirmation": "estimated_times"})
    print(response.json())

In [204]:
estimated_time_df = pd.read_csv(CSV_PATH + "estimated_time.csv")
estimated_time_df.head()

Empty DataFrame
Columns: [id, vertex_id, order_id, shipment_time, event_time, estimation_time, DT, PT_lower, PT_n_paths, PT_avg_tmi, PT_avg_wmi, PT_upperTT_lower, TT_upper, TFST_lower, TFST_upper, EST, EODT, CFDI_lower, CFDI_upper, EDD, time_deviation_id, alpha_id, pt_confidence, tt_confidence]
Index: []

[0 rows x 24 columns]

In [205]:
assert not estimated_time_df.isna().any().any()
assert len(estimated_time_df) == 0

#### Data preparation

In [206]:
orders_df.head()

id  manufacturer_id  manufacturer_order_id  site_id  carrier_id     status  \
0   1                1                   6004        8           1  DELIVERED   
1   2                1                   6005        1           2  DELIVERED   
2   3                1                   6037        3           2  DELIVERED   
3   4                1                   6045        3           2  DELIVERED   
4   5                1                   6046        4           3  DELIVERED   

   n_steps                                      tracking_link  \
0       14  https://mydhl.express.dhl/it/it/tracking.html#...   
1       11                                 1Z60699Y0400391867   
2       11                                 1ZR465910413218509   
3       12  https://www.digikey.it/OrderHistory/shipmenttr...   
4       14  https://www.fedex.com/fedextrack/?trknbr=43744...   

      tracking_number manufacturer_creation_timestamp  \
0          1656325344       2025-01-07T07:31:00+00:00   
1  1Z60699Y0400391867       2025-01-07T13:57:00+00:00   
2  1ZR465910413218509       2025-01-10T13:41:00+00:00   
3  1ZR465910413219320       2025-01-13T15:27:00+00:00   
4        437446419489       2025-01-13T15:27:00+00:00   

  manufacturer_estimated_delivery_timestamp  \
0                 2025-01-13 22:00:00+00:00   
1                 2025-01-08 22:00:00+00:00   
2                 2025-01-14 22:00:00+00:00   
3                 2025-01-15 22:00:00+00:00   
4                 2025-01-15 22:00:00+00:00   

  manufacturer_confirmed_delivery_timestamp carrier_creation_timestamp  \
0                 2025-01-17 11:36:00+00:00  2025-01-14T09:16:00+00:00   
1                 2025-01-13 12:47:00+00:00  2025-01-09T03:11:00+00:00   
2                 2025-01-15 09:18:00+00:00  2025-01-11T00:10:00+00:00   
3                 2025-01-15 09:45:00+00:00  2025-01-13T17:08:00+00:00   
4                 2025-01-15 12:14:00+00:00  2025-01-13T20:15:00+00:00   

  carrier_estimated_delivery_timestamp carrier_confirmed_delivery_timestamp  \
0                                 None            2025-01-17T10:40:00+00:00   
1                                 None            2025-01-13T09:19:00+00:00   
2                                 None            2025-01-15T09:47:00+00:00   
3                                 None            2025-01-15T09:47:00+00:00   
4                                 None            2025-01-15T11:49:00+00:00   

   SLS  SRS  
0    0    0  
1    0    0  
2    0    0  
3    0    0  
4    0    0

In [207]:
vertices_df.head()

id                    name           type
0   1     WARSAW, MAZOVIA, PL   INTERMEDIATE
1   2                       3  SUPPLIER_SITE
2   3    CINCINNATI, OHIO, US   INTERMEDIATE
3   4  ISTANBUL, ISTANBUL, TR   INTERMEDIATE
4   5                       8  SUPPLIER_SITE

In [208]:
manufacturer_name = manufacturers_df.loc[0, 'name']
manufacturer_name

'FAE'

In [209]:
vertex_name_map = {}

for _, row in vertices_df.iterrows():
    if row['type'] == 'MANUFACTURER':
        vertex_name_map[manufacturer_name] = row['id'] 
    vertex_name_map[row['name']] = row['id']

vertex_name_map

{'WARSAW, MAZOVIA, PL': 1,
 '3': 2,
 'CINCINNATI, OHIO, US': 3,
 'ISTANBUL, ISTANBUL, TR': 4,
 '8': 5,
 'BOCA RATON, FLORIDA, US': 6,
 'COLOGNE, NORTH RHINE-WESTPHALIA, DE': 7,
 '5': 8,
 'BALERNA, TICINO, CH': 9,
 '7': 10,
 '11': 11,
 'NEW DELHI, DELHI, IN': 12,
 '13': 13,
 '15': 14,
 'BRATISLAVA, BRATISLAVA REGION, SK': 15,
 'MINNEAPOLIS, MINNESOTA, US': 16,
 'GRASSOBBIO, LOMBARDY, IT': 17,
 '18': 18,
 'LEIPZIG, SAXONY, DE': 19,
 'BRUSSELS, BRUSSELS CAPITAL, BE': 20,
 '4': 21,
 'GRAND PRAIRIE, TEXAS, US': 22,
 'SERIATE, LOMBARDY, IT': 23,
 'LONDON, ENGLAND, GB': 24,
 'NEW YORK, NEW YORK, US': 25,
 'FRANKFURT AM MAIN, HESSE, DE': 26,
 'GDANSK, POMERANIA, PL': 27,
 'NEWARK, DELAWARE, US': 28,
 'SAN JOSÉ, SAN JOSÉ, CR': 29,
 '16': 30,
 '1': 34,
 'GUANGZHOU, GUANGDONG, CN': 32,
 '10': 33,
 'FAE': 34,
 '12': 35,
 'TSUEN WAN, TSUEN WAN, HK': 36,
 'THIEF RIVER FALLS, MINNESOTA, US': 37,
 '21': 38,
 'SHENZHEN, GUANGDONG, CN': 39,
 'BRESCIA, LOMBARDY, IT': 40,
 'MANSFIELD, TEXAS, US': 41,
 'MO

In [210]:
order_steps_enriched_df = pd.read_csv(CSV_PATH + "order_steps_enriched_train.csv")
order_steps_enriched_df.head()

order_id  step_source           timestamp_source          location_source  \
0         1            1  2025-01-14 09:16:00+00:00  DONGGUAN, GUANGDONG, CN   
1         1            2  2025-01-14 17:40:00+00:00  DONGGUAN, GUANGDONG, CN   
2         1            3  2025-01-14 18:05:00+00:00  DONGGUAN, GUANGDONG, CN   
3         1            4  2025-01-14 21:46:00+00:00  SHENZHEN, GUANGDONG, CN   
4         1            5  2025-01-16 04:03:00+00:00  SHENZHEN, GUANGDONG, CN   

   step_destination      timestamp_destination  \
0                 2  2025-01-14 17:40:00+00:00   
1                 3  2025-01-14 18:05:00+00:00   
2                 4  2025-01-14 21:46:00+00:00   
3                 5  2025-01-16 04:03:00+00:00   
4                 6  2025-01-16 23:01:00+00:00   

             location_destination      hours  geodesic_km  distance_road_km  \
0         DONGGUAN, GUANGDONG, CN   8.400000     0.000000             0.000   
1         DONGGUAN, GUANGDONG, CN   0.416667     0.000000             0.000   
2         SHENZHEN, GUANGDONG, CN   3.683333    61.761066           107.745   
3         SHENZHEN, GUANGDONG, CN  30.283333     0.000000             0.000   
4  BRUSSELS, BRUSSELS CAPITAL, BE  18.966667  9381.875452             0.000   

   time_road_no_traffic_hours  time_road_traffic_hours  
0                    0.000000                 0.000000  
1                    0.000000                 0.000000  
2                    2.115278                 2.115278  
3                    0.000000                 0.000000  
4                    0.000000                 0.000000

In [211]:
if len(orders_df) < len(order_steps_enriched_df["order_id"].unique()):
    print("Missing orders")
    order_steps_enriched_df = order_steps_enriched_df[order_steps_enriched_df["order_id"].isin(orders_df["id"].values)]

#order_steps_enriched_df: pd.DataFrame = order_steps_enriched_df.drop(columns=["tmi", "wmi", "transportation_mode"]) 

assert not order_steps_enriched_df.isna().any().any()
assert len(order_steps_enriched_df["order_id"].unique()) == len(orders_df)

In [212]:
order_steps_enriched_df

order_id  step_source           timestamp_source  \
0           1            1  2025-01-14 09:16:00+00:00   
1           1            2  2025-01-14 17:40:00+00:00   
2           1            3  2025-01-14 18:05:00+00:00   
3           1            4  2025-01-14 21:46:00+00:00   
4           1            5  2025-01-16 04:03:00+00:00   
..        ...          ...                        ...   
931       106            7  2025-07-23 00:45:00+00:00   
932       106            8  2025-07-23 02:08:00+00:00   
933       106            9  2025-07-23 03:40:00+00:00   
934       106           10  2025-07-23 03:53:00+00:00   
935       106           11  2025-07-23 04:02:00+00:00   

                         location_source  step_destination  \
0                DONGGUAN, GUANGDONG, CN                 2   
1                DONGGUAN, GUANGDONG, CN                 3   
2                DONGGUAN, GUANGDONG, CN                 4   
3                SHENZHEN, GUANGDONG, CN                 5   
4                SHENZHEN, GUANGDONG, CN                 6   
..                                   ...               ...   
931  COLOGNE, NORTH RHINE-WESTPHALIA, DE                 8   
932                SERIATE, LOMBARDY, IT                 9   
933                SERIATE, LOMBARDY, IT                10   
934               TREVIOLO, LOMBARDY, IT                11   
935               TREVIOLO, LOMBARDY, IT                12   

         timestamp_destination            location_destination      hours  \
0    2025-01-14 17:40:00+00:00         DONGGUAN, GUANGDONG, CN   8.400000   
1    2025-01-14 18:05:00+00:00         DONGGUAN, GUANGDONG, CN   0.416667   
2    2025-01-14 21:46:00+00:00         SHENZHEN, GUANGDONG, CN   3.683333   
3    2025-01-16 04:03:00+00:00         SHENZHEN, GUANGDONG, CN  30.283333   
4    2025-01-16 23:01:00+00:00  BRUSSELS, BRUSSELS CAPITAL, BE  18.966667   
..                         ...                             ...        ...   
931  2025-07-23 02:08:00+00:00           SERIATE, LOMBARDY, IT   1.383333   
932  2025-07-23 03:40:00+00:00           SERIATE, LOMBARDY, IT   1.533333   
933  2025-07-23 03:53:00+00:00          TREVIOLO, LOMBARDY, IT   0.216667   
934  2025-07-23 04:02:00+00:00          TREVIOLO, LOMBARDY, IT   0.150000   
935  2025-07-23 08:21:00+00:00         GAZZANIGA, LOMBARDY, IT   4.316667   

     geodesic_km  distance_road_km  time_road_no_traffic_hours  \
0       0.000000             0.000                    0.000000   
1       0.000000             0.000                    0.000000   
2      61.761066           107.745                    2.115278   
3       0.000000             0.000                    0.000000   
4    9381.875452             0.000                    0.000000   
..           ...               ...                         ...   
931   618.678048           875.476                    9.301389   
932     0.000000             0.000                    0.000000   
933     8.892137            11.636                    0.244722   
934     0.000000             0.000                    0.000000   
935    21.550816            30.292                    0.481667   

     time_road_traffic_hours  
0                   0.000000  
1                   0.000000  
2                   2.115278  
3                   0.000000  
4                   0.000000  
..                       ...  
931                 9.717778  
932                 0.000000  
933                 0.250556  
934                 0.000000  
935                 0.502222  

[936 rows x 12 columns]

In [213]:
orders_df["id"].values

array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  13,  14,
        15,  16,  17,  18,  19,  21,  22,  24,  25,  26,  27,  28,  29,
        30,  31,  33,  34,  35,  36,  37,  38,  39,  40,  41,  42,  43,
        45,  46,  47,  48,  49,  50,  51,  52,  55,  56,  57,  59,  61,
        62,  63,  64,  65,  66,  67,  68,  69,  70,  74,  76,  77,  78,
        79,  80,  81,  82,  83,  85,  86,  87,  88,  89,  90,  91,  92,
        94,  95,  97,  99, 101, 102, 103, 104, 105, 106])

In [214]:
from typing import List, Dict
from datetime import datetime

estimated_time_request_data: List[Dict] = []

for _, row in order_steps_enriched_df.iterrows():
    #if row["location_source"] == row["location_destination"]:       # Skip vertex times
    #    continue

    order_id: int = row["order_id"]
    order: pd.Series = orders_df[orders_df["id"] == order_id].iloc[0]
    if row['step_source'] == 1:
        site_id: int = order.loc["site_id"]
        v_id: str = vertex_name_map[str(site_id)]
    else:
        v_id: str = vertex_name_map[row["location_source"]]
    
    event_time: str = row["timestamp_source"]
    event_dt: datetime = datetime.fromisoformat(event_time)

    estimated_time_request_data.append({
        "vertex_id": v_id,
        "order_id": order_id,
        "event_time": event_dt.isoformat(),
        "estimation_time": event_dt.isoformat()       # Compute the estimation as soon as the event occurs
    })

    if row['step_destination'] == order["n_steps"]:
        v_id: str = vertex_name_map[manufacturer_name]
        event_time: str = row["timestamp_destination"]
        event_dt: datetime = datetime.fromisoformat(event_time)
        estimated_time_request_data.append({
            "vertex_id": v_id,
            "order_id": order_id,
            "event_time": event_dt.isoformat(),
            "estimation_time": event_dt.isoformat()       # Compute the estimation as soon as the event occurs
        })

estimated_time_request_data

[{'vertex_id': 5,
  'order_id': 1,
  'event_time': '2025-01-14T09:16:00+00:00',
  'estimation_time': '2025-01-14T09:16:00+00:00'},
 {'vertex_id': 63,
  'order_id': 1,
  'event_time': '2025-01-14T17:40:00+00:00',
  'estimation_time': '2025-01-14T17:40:00+00:00'},
 {'vertex_id': 63,
  'order_id': 1,
  'event_time': '2025-01-14T18:05:00+00:00',
  'estimation_time': '2025-01-14T18:05:00+00:00'},
 {'vertex_id': 39,
  'order_id': 1,
  'event_time': '2025-01-14T21:46:00+00:00',
  'estimation_time': '2025-01-14T21:46:00+00:00'},
 {'vertex_id': 39,
  'order_id': 1,
  'event_time': '2025-01-16T04:03:00+00:00',
  'estimation_time': '2025-01-16T04:03:00+00:00'},
 {'vertex_id': 20,
  'order_id': 1,
  'event_time': '2025-01-16T23:01:00+00:00',
  'estimation_time': '2025-01-16T23:01:00+00:00'},
 {'vertex_id': 20,
  'order_id': 1,
  'event_time': '2025-01-16T23:02:00+00:00',
  'estimation_time': '2025-01-16T23:02:00+00:00'},
 {'vertex_id': 19,
  'order_id': 1,
  'event_time': '2025-01-17T01:01:00+00:0

In [215]:
estimated_time_df = pd.DataFrame(estimated_time_request_data)
estimated_time_df

vertex_id  order_id                 event_time  \
0             5         1  2025-01-14T09:16:00+00:00   
1            63         1  2025-01-14T17:40:00+00:00   
2            63         1  2025-01-14T18:05:00+00:00   
3            39         1  2025-01-14T21:46:00+00:00   
4            39         1  2025-01-16T04:03:00+00:00   
...         ...       ...                        ...   
1019         23       106  2025-07-23T02:08:00+00:00   
1020         23       106  2025-07-23T03:40:00+00:00   
1021         60       106  2025-07-23T03:53:00+00:00   
1022         60       106  2025-07-23T04:02:00+00:00   
1023         34       106  2025-07-23T08:21:00+00:00   

                estimation_time  
0     2025-01-14T09:16:00+00:00  
1     2025-01-14T17:40:00+00:00  
2     2025-01-14T18:05:00+00:00  
3     2025-01-14T21:46:00+00:00  
4     2025-01-16T04:03:00+00:00  
...                         ...  
1019  2025-07-23T02:08:00+00:00  
1020  2025-07-23T03:40:00+00:00  
1021  2025-07-23T03:53:00+00:00  
1022  2025-07-23T04:02:00+00:00  
1023  2025-07-23T08:21:00+00:00  

[1024 rows x 4 columns]

In [216]:
assert not estimated_time_df.isna().any().any()

In [217]:
len(estimated_time_request_data)

1024

#### Post

In [218]:
endpoint = "lcdi/realtime"

In [219]:
orders_to_post = set([i for i in range(1, 6)])
request_data_df = estimated_time_df[estimated_time_df["order_id"].isin(orders_to_post)]
request_data_df.shape

(62, 4)

In [220]:
request_data = []
for i, row in request_data_df.iterrows():
    request_data.append({
        "vertex": {"vertex_id": row["vertex_id"]},
        "order_id": row["order_id"],
        "event_time": row["event_time"],
        "estimation_time": row["estimation_time"]
    })
assert len(request_data) == len(request_data_df)
request_data

[{'vertex': {'vertex_id': 5},
  'order_id': 1,
  'event_time': '2025-01-14T09:16:00+00:00',
  'estimation_time': '2025-01-14T09:16:00+00:00'},
 {'vertex': {'vertex_id': 63},
  'order_id': 1,
  'event_time': '2025-01-14T17:40:00+00:00',
  'estimation_time': '2025-01-14T17:40:00+00:00'},
 {'vertex': {'vertex_id': 63},
  'order_id': 1,
  'event_time': '2025-01-14T18:05:00+00:00',
  'estimation_time': '2025-01-14T18:05:00+00:00'},
 {'vertex': {'vertex_id': 39},
  'order_id': 1,
  'event_time': '2025-01-14T21:46:00+00:00',
  'estimation_time': '2025-01-14T21:46:00+00:00'},
 {'vertex': {'vertex_id': 39},
  'order_id': 1,
  'event_time': '2025-01-16T04:03:00+00:00',
  'estimation_time': '2025-01-16T04:03:00+00:00'},
 {'vertex': {'vertex_id': 20},
  'order_id': 1,
  'event_time': '2025-01-16T23:01:00+00:00',
  'estimation_time': '2025-01-16T23:01:00+00:00'},
 {'vertex': {'vertex_id': 20},
  'order_id': 1,
  'event_time': '2025-01-16T23:02:00+00:00',
  'estimation_time': '2025-01-16T23:02:00+00

In [221]:
CHUNK_SIZE = 2      # 5 for warm starts, 2 for cold starts
MAX_WORKERS = 10

def process_chunk(index: int, chunk: List, n: int) -> Tuple[float, List]:
    print(f"Processing chunk {index}/{n} ({(index) / n * 100:.2f}%) of size {len(chunk)}")
    now = datetime.now()
    response = post_request(endpoint, chunk)
    elapsed_time = (datetime.now() - now).total_seconds()
    norm_elapsed_time = elapsed_time / len(chunk) * CHUNK_SIZE
    print(f"\tChunk {index} processed: {len(chunk)} items, took {elapsed_time:.2f} seconds (norm. {norm_elapsed_time:.2f} seconds)")
    assert isinstance(response, list), "Response should be a list"
    return norm_elapsed_time, response

In [222]:
times_data: List[float] = []
estimations: List = []

chunks: List[List] = list(chunked(request_data, CHUNK_SIZE))
len(chunks), len(chunks[0]), len(chunks[-1])

(31, 2, 2)

Lambda warming:

In [223]:
def warm_lambda(url):
    q_params = {"order": 1}
    response = requests.get(url, params=q_params)
    response.raise_for_status()

In [224]:
warm_lambda(BASE_URL + "lcdi/realtime")

In [225]:
now = datetime.now()
with ThreadPoolExecutor(max_workers=MAX_WORKERS) as executor:
    futures = [
        executor.submit(process_chunk, i, chunk, len(chunks))
        for i, chunk in enumerate(chunks)
    ]

    for future in as_completed(futures):
        norm_elapsed_time, response = future.result()
        times_data.append(norm_elapsed_time)
        estimations.extend(response)

assert len(estimations) == len(request_data)

times: np.ndarray = np.array(times_data)
elapsed = (datetime.now() - now).total_seconds()

print()
print(f"Total elapsed time: {elapsed:.2f} seconds")
print(f"Mean processing time: {np.mean(times):.2f} seconds")
print(f"Std processing time: {np.std(times):.2f} seconds")
print(f"Minimum processing time: {np.min(times):.2f} seconds for chunk {np.argmin(times)}")
print(f"Maximum processing time: {np.max(times):.2f} seconds for chunk {np.argmax(times)}")

Processing chunk 0/31 (0.00%) of size 2
Processing chunk 1/31 (3.23%) of size 2
Processing chunk 2/31 (6.45%) of size 2
Processing chunk 3/31 (9.68%) of size 2
Processing chunk 4/31 (12.90%) of size 2
Processing chunk 5/31 (16.13%) of size 2
Processing chunk 6/31 (19.35%) of size 2
Processing chunk 7/31 (22.58%) of size 2
Processing chunk 8/31 (25.81%) of size 2
Processing chunk 9/31 (29.03%) of size 2
	Chunk 2 processed: 2 items, took 1.95 seconds (norm. 1.95 seconds)
Processing chunk 10/31 (32.26%) of size 2
	Chunk 10 processed: 2 items, took 1.55 seconds (norm. 1.55 seconds)
Processing chunk 11/31 (35.48%) of size 2
	Chunk 11 processed: 2 items, took 1.52 seconds (norm. 1.52 seconds)
Processing chunk 12/31 (38.71%) of size 2
	Chunk 12 processed: 2 items, took 2.05 seconds (norm. 2.05 seconds)
Processing chunk 13/31 (41.94%) of size 2
	Chunk 13 processed: 2 items, took 1.54 seconds (norm. 1.54 seconds)
Processing chunk 14/31 (45.16%) of size 2
	Chunk 0 processed: 2 items, took 8.70 s

In [226]:
response = send_request(endpoint)
response

[{'order_id': 1,
  'manufacturer_order_id': 6004,
  'tracking_number': '1656325344',
  'site': {'id': 8, 'location': 'DONGGUAN, GUANGDONG, CN'},
  'supplier': {'id': 5, 'manufacturer_id': 6004, 'name': 'SAFE'},
  'carrier': {'id': 1, 'name': 'DHL Express'},
  'manufacturer': {'id': 1,
   'name': 'FAE',
   'location': 'GAZZANIGA, LOMBARDY, IT'},
  'SLS': False,
  'SRS': False,
  'EODT': 243.15,
  'EDD': '2025-01-17T10:40:00+00:00',
  'delay': {'dispatch': {'lower': 35.866667, 'upper': 35.866667},
   'shipment': {'lower': 0.0, 'upper': 0.0},
   'total': {'lower': 35.866667, 'upper': 35.866667}},
  'status': 'DELIVERED',
  'data': [{'id': 9,
    'vertex': {'id': 5, 'name': '8', 'type': 'SUPPLIER_SITE'},
    'order_time': '2025-01-07T07:31:00+00:00',
    'shipment_time': '2025-01-14T09:16:00+00:00',
    'event_time': '2025-01-14T09:16:00+00:00',
    'estimation_time': '2025-01-14T09:16:00+00:00',
    'status': 'IN_TRANSIT',
    'indicators': {'parameters': {'DT': {'holidays': {'consider_cl

### All tables

In [227]:
endpoint = "/db/tables"

data = send_request(endpoint)
data

{'success': True,
 'message': 'Retrieved info for 36 tables',
 'data': {'totalTables': 36,
  'tables': [{'tableName': 'alphas', 'rowCount': 62},
   {'tableName': 'alphas_opt', 'rowCount': 420},
   {'tableName': 'carriers', 'rowCount': 20},
   {'tableName': 'countries', 'rowCount': 230},
   {'tableName': 'dispatch_time_gammas', 'rowCount': 1},
   {'tableName': 'dispatch_time_samples', 'rowCount': 20},
   {'tableName': 'dispatch_times', 'rowCount': 86},
   {'tableName': 'disruptions', 'rowCount': 0},
   {'tableName': 'estimated_times', 'rowCount': 62},
   {'tableName': 'estimated_times_holidays', 'rowCount': 11},
   {'tableName': 'estimation_params', 'rowCount': 62},
   {'tableName': 'holidays', 'rowCount': 3609},
   {'tableName': 'kafka_disruption', 'rowCount': 0},
   {'tableName': 'locations', 'rowCount': 45},
   {'tableName': 'manufacturers', 'rowCount': 1},
   {'tableName': 'order_step_weather_data', 'rowCount': 0},
   {'tableName': 'order_steps', 'rowCount': 0},
   {'tableName': 'or